In [1]:
import keras
from keras import applications
from keras.preprocessing.image import ImageDataGenerator
from keras import optimizers
from keras.models import Sequential, Model 
from keras.layers import Dropout, Flatten, Dense, GlobalAveragePooling2D
from keras import backend as k 
from keras.callbacks import CSVLogger, ModelCheckpoint, LearningRateScheduler, TensorBoard, EarlyStopping
from keras import optimizers
from keras.preprocessing.image import ImageDataGenerator, array_to_img, img_to_array, load_img
from keras.utils.vis_utils import plot_model
from keras.applications.mobilenet_v2 import decode_predictions
from keras.layers.normalization import BatchNormalization

from keras.models import Sequential
from keras.layers import Conv2D, MaxPooling2D
from keras.layers import Activation, Dropout, Flatten, Dense

import matplotlib.image as mpimg
import matplotlib.pyplot as plt
import numpy as np
import os

import tensorflow
from time import time

import pandas

import pickle as pk

from keras.wrappers.scikit_learn import KerasClassifier

import numpy as np

seed = 7

Using TensorFlow backend.


## Evaluate Batch size with RMSprop.
#### First, evaluate each size independently (restart kernel each time without clearing output).
#### Then, to the, all sequential to get approximation of the weights really fast and improve accuracy sequentially

In [2]:
from tensorflow.python.client import device_lib
print(device_lib.list_local_devices())

[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 13579028716821849799
, name: "/device:GPU:0"
device_type: "GPU"
memory_limit: 11172849255
locality {
  bus_id: 1
  links {
  }
}
incarnation: 6736084743377311626
physical_device_desc: "device: 0, name: Tesla K80, pci bus id: 0000:00:1e.0, compute capability: 3.7"
]


In [3]:
dir(keras.applications.mobilenet_v2)

['MobileNetV2',
 '__builtins__',
 '__cached__',
 '__doc__',
 '__file__',
 '__loader__',
 '__name__',
 '__package__',
 '__spec__',
 'absolute_import',
 'decode_predictions',
 'division',
 'keras_modules_injection',
 'mobilenet_v2',
 'preprocess_input',
 'print_function']

In [4]:
np.random.seed(seed)

In [5]:
data_dir = '/data/oxford102/train'
train_data_dir = "/data/oxford102/train/"
validation_data_dir = "/data/oxford102/train/"
img_width, img_height = 256, 256
# batch_size = 32
epochs = 100
nr_categories = 102
nb_train_samples = 4604
nb_validation_samples = 1094 

In [6]:
# train_val_datagen = ImageDataGenerator(preprocessing_function=input_processor, 
#                                            validation_split=0.2)

# train_val_datagen_aug = ImageDataGenerator(
#         #rescale=1. / 255,
#         rotation_range=40,
#         width_shift_range=0.2,
#         height_shift_range=0.2,
#         shear_range=0.2,
#         zoom_range=0.2,
#         horizontal_flip=True,
#         fill_mode='nearest',
#         preprocessing_function=input_processor,
#         validation_split=0.2)

In [7]:
def get_image_generator(input_processor, img_aug=False):
    if not img_aug:
        train_val_datagen = ImageDataGenerator(preprocessing_function=input_processor, 
                                           validation_split=0.2)
    else: 
        train_val_datagen = ImageDataGenerator(
            rotation_range=40,
            width_shift_range=0.2,
            height_shift_range=0.2,
            shear_range=0.2,
            zoom_range=0.2,
            horizontal_flip=True,
            fill_mode='nearest',
            preprocessing_function=input_processor,
            validation_split=0.2)
        
    return train_val_datagen

In [8]:
def get_generators(batch_size, image_size, input_processor, img_aug=False):

    img_width, img_height = image_size
    
    train_val_datagen = get_image_generator(input_processor, img_aug)

    train_generator = train_val_datagen.flow_from_directory(
            train_data_dir,  # this is the target directory
            target_size=(img_width, img_height),  # all images will be resized to 250x250
            batch_size=batch_size,
            subset="training",
            class_mode='categorical')

    validation_generator = train_val_datagen.flow_from_directory(
            train_data_dir,  # this is the target directory
            target_size=(img_width, img_height),  # all images will be resized to 250x250
            subset="validation",
            batch_size=batch_size,
            class_mode='categorical')
    
    return train_generator, validation_generator


In [9]:
#from keras import regularizers

def get_model(network_name="inception_resnet_v2", image_size=(256, 256), verbose=False):
    k.set_learning_phase(0)

    img_width, img_height = image_size
    if network_name == "vgg16":
        base_model = keras.applications.vgg16.VGG16(weights = "imagenet", include_top=False, input_shape = (img_width, img_height, 3))
        input_processor = applications.vgg16.preprocess_input
    elif network_name == "vgg19":
        base_model = keras.applications.vgg19.VGG19(weights = "imagenet", include_top=False, input_shape = (img_width, img_height, 3))
        input_processor = applications.vgg19.preprocess_input
    elif network_name == "inception_resnet_v2":
        base_model = keras.applications.inception_resnet_v2.InceptionResNetV2(weights = "imagenet", include_top=False, input_shape = (img_width, img_height, 3))
        input_processor = applications.inception_resnet_v2.preprocess_input
    elif network_name == "mobilenet_v2":
        base_model = keras.applications.mobilenet_v2.MobileNetV2(weights = "imagenet", include_top=False, input_shape = (img_width, img_height, 3))
        input_processor = applications.mobilenet_v2.preprocess_input
    else:
        raise Exception("check your network name")

    for layer in base_model.layers[:]:
        layer.trainable = False

        #Adding custom Layers 
    k.set_learning_phase(1)
    x = base_model.output
    x = Flatten()(x)
    x = Dense(1024, activation="relu", 
              #kernel_regularizer=regularizers.l2(0.01),
             #       activity_regularizer=regularizers.l1(0.001)
             )(x)
    x = Dropout(0.5)(x)
    x = BatchNormalization()(x, training=True)
    #x = Dense(102, activation="relu")(x)
    predictions = Dense(nr_categories, activation="softmax")(x)

    _model = Model(input = base_model.input, output = predictions)
    if verbose:
        _model.summary()
    return _model, input_processor

In [9]:
# _model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001, rho=0.9, epsilon=None, decay=0.0), metrics=["accuracy"])


# With data augmentation

In [10]:
#run_training(model_name, _model, train_generator, validation_generator, params, num_train_img, num_val_img):
    
def train_my_model(train_generator, val_generator, params, _model):
    model_name = "mobilenet_v2"
    num_train_img = 4604
    num_val_img = 1094
#     params = {'network_name': model_name,
#              'image_aug': True,
#              'optimizer': 'SGD',
#              'optimizer_params': None, 
#              'batch_size': 128,
#              'epochs': 100,
#              'image_size': (256, 256),
#              'log_time': None}


    np.random.seed(seed)
    log_time = time()
    params['log_time'] = log_time
    batch_size = params.get("batch_size")

    print(params["optimizer"])
    _model.compile(loss = "categorical_crossentropy", optimizer = params["optimizer"], metrics=["accuracy"])


    base = '/data/oxford102/experiments'
    path = os.path.join(base, str(log_time))
    checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
    early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
    tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
    csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

    try:
        if not os.path.exists(path):
            os.makedirs(path)
        history_callback = _model.fit_generator(
                train_generator,
                steps_per_epoch=num_train_img // batch_size,
                epochs=params['epochs'],
                validation_data=validation_generator,
                validation_steps=num_val_img // params['batch_size'],
                callbacks = [checkpoint, early, tensorboard, csv_logger])
    except Exception as e:
        raise(e)
    finally:
        pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
        _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
        print(params)
        params

    return _model, history_callback

# Without data augmentation

In [12]:
#run_training(model_name, _model, train_generator, validation_generator, params, num_train_img, num_val_img):
    

model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': model_name,
         'image_aug': True,
         'optimizer': 'SGD',
         'optimizer_params': None, 
         'batch_size': 128,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.SGD(lr=0.001, momentum=0.9), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
35/35 [==============================] - 29s 841ms/step - loss: 4.1591 - acc: 0.1473 - val_loss: 3.5489 - val_acc: 0.1992

Epoch 00001: val_acc improved from -inf to 0.19922, saving model to /data/oxford102/experiments/1544921965.6249993/mobilenet_v2_1544921965.6249993.h5
Epoch 2/100
35/35 [==============================] - 23s 654ms/step - loss: 3.1554 - acc: 0.2786 - val_loss: 2.9939 - val_acc: 0.2734

Epoch 00002: val_acc improved from 0.19922 to 0.27344, saving model to /data/oxford102/experiments/1544921965.6249993/mobilenet_v2_1544921965.6249993.h5
Epoch 3/100
35/35 [==============================] - 23s 656ms/step - loss: 2.7947 - acc: 0.3366 - val_loss: 2.5649 - val_acc: 0.3867

Epoch 00003: val_acc improved from 0.27344 to 0.38672, saving model to /data/oxford102/experiments/1544921965.6249993/mobilenet_v2_1544921965.6249993.h5
Epoch 4/100
35/35 [==============================] - 23s 652ms/step - loss: 2.5564 - acc: 0.3964 - val_loss: 2.4116 - val_acc: 0.4219

Epoc

In [ ]:
# Hyperparameter optimization

In [ ]:
optimizers

In [ ]:
optimizers.SGD(lr=0.01, decay=1e-6, momentum=0.9, nesterov=True)

In [ ]:
optimizers.SGD(lr=0.01, momentum=0.0, decay=0.0, nesterov=False)

In [ ]:
optimizers.RMSprop(lr=0.001, rho=0.9, epsilon=None, decay=0.0)

In [ ]:
optimizers.Adagrad(lr=0.01, epsilon=None, decay=0.0)

In [ ]:
optimizers.Adadelta(lr=1.0, rho=0.95, epsilon=None, decay=0.0)

In [ ]:
optimizers.Adam(lr=0.001, beta_1=0.9, beta_2=0.999, epsilon=None, decay=0.0, amsgrad=False)

In [ ]:
optimizers.Adamax(lr=0.002, beta_1=0.9, beta_2=0.999, epsilon=None, decay=0.0)

In [ ]:
optimizers.Nadam(lr=0.002, beta_1=0.9, beta_2=0.999, epsilon=None, schedule_decay=0.004)

In [13]:
import talos as ta

In [ ]:
p = {'lr': (0.001, 0.01, 0.1),
     'batch_size': (128),
     'epochs': [150],
     'dropout': (0, 0.5, 5),
     'weight_regulizer':[None],
     'emb_output_dims': [None],
     'shape':['brick','long_funnel'],
     'optimizer': [Adam, Nadam, RMSprop],
     'losses': [logcosh, binary_crossentropy],
     'activation':[relu, elu],
     'last_activation': [sigmoid]}

In [ ]:
model = get_model(params)
train_my_model()

In [10]:
def train_model(params, _model, generators):
    model_name = params["network_name"]
    num_train_img = 4604
    num_val_img = 1094

    np.random.seed(seed)
    log_time = time()
    params['log_time'] = log_time
    batch_size = params.get("batch_size")

    train_generator, validation_generator = generators
    _model.compile(loss = "categorical_crossentropy", optimizer = params["optimizer"], metrics=["accuracy"])


    base = '/data/oxford102/experiments'
    path = os.path.join(base, str(log_time))
    checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
    early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
    tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
    csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

    try:
        if not os.path.exists(path):
            os.makedirs(path)
        history_callback = _model.fit_generator(
                train_generator,
                steps_per_epoch=num_train_img // params["batch_size"] // 2,
                epochs=params["epochs"],
                validation_data=validation_generator,
                validation_steps=num_val_img // params["batch_size"],
                callbacks = [checkpoint, early, tensorboard, csv_logger])
    except Exception as e:
        raise(e)
    finally:
        params.pop("optimizer")
        pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
        _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
        print(params)
        params

In [18]:
print(10)

10


In [33]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 256,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(batch_size, params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

80142336/80134624 [==============================] - 2s 0us/step


/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

TypeError: can't pickle _thread.RLock objects

In [13]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 512,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

ResourceExhaustedError: OOM when allocating tensor with shape[512,64,256,256] and type float on /job:localhost/replica:0/task:0/device:GPU:0 by allocator GPU_0_bfc
	 [[{{node block1_conv1/convolution}} = Conv2D[T=DT_FLOAT, data_format="NCHW", dilations=[1, 1, 1, 1], padding="SAME", strides=[1, 1, 1, 1], use_cudnn_on_gpu=true, _device="/job:localhost/replica:0/task:0/device:GPU:0"](block1_conv1/convolution-0-TransposeNHWCToNCHW-LayoutOptimizer, block1_conv1/kernel/read)]]
Hint: If you want to see a list of allocated tensors when OOM happens, add report_tensor_allocations_upon_oom to RunOptions for current allocation info.

	 [[{{node loss/mul/_283}} = _Recv[client_terminated=false, recv_device="/job:localhost/replica:0/task:0/device:CPU:0", send_device="/job:localhost/replica:0/task:0/device:GPU:0", send_device_incarnation=1, tensor_name="edge_834_loss/mul", tensor_type=DT_FLOAT, _device="/job:localhost/replica:0/task:0/device:CPU:0"]()]]
Hint: If you want to see a list of allocated ten

In [14]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 128,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

In [17]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 64,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_5 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

In [15]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 32,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

In [16]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 16,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_4 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

In [18]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 8,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_6 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

{'network_name': 'vgg19', 'image_aug': False, 'optimizer_name': 'RMSprop', 'optimizer_params': None, 'batch_size': 8, 'epochs': 100, 'image_size': (256, 256), 'log_time': 1545013813.496132}


# SGD

In [12]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.0, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 256,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

ResourceExhaustedError: OOM when allocating tensor with shape[256,64,256,256] and type float on /job:localhost/replica:0/task:0/device:GPU:0 by allocator GPU_0_bfc
	 [[{{node block1_conv2/convolution}} = Conv2D[T=DT_FLOAT, data_format="NCHW", dilations=[1, 1, 1, 1], padding="SAME", strides=[1, 1, 1, 1], use_cudnn_on_gpu=true, _device="/job:localhost/replica:0/task:0/device:GPU:0"](block1_conv1/Relu, block1_conv2/kernel/read)]]
Hint: If you want to see a list of allocated tensors when OOM happens, add report_tensor_allocations_upon_oom to RunOptions for current allocation info.


In [13]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.0, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 128,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

In [14]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.0, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 64,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

In [15]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.0, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 32,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_4 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

In [16]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.0, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 16,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_5 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

In [17]:
#inception_resnet_v2, vgg16, vgg19

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.0, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 8,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_6 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

In [18]:
print("DONE")

DONE


# inception_resnet_v2 RMSProp

In [14]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 256,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_2 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_204 (Conv2D)             (None, 127, 127, 32) 864         input_2[0][0]                    
__________________________________________________________________________________________________
batch_normalization_205 (BatchN (None, 127, 127, 32) 96          conv2d_204[0][0]                 
__________________________________________________________________________________________________
activation_204 (Activation)     (None, 127, 127, 32) 0           batch_normalization_205[0][0]    
__________________________________________________________________________________________________
conv2d_205

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 91s 5s/step - loss: 2.8596 - acc: 0.3658 - val_loss: 1.9975 - val_acc: 0.5020

Epoch 00001: val_acc improved from -inf to 0.50195, saving model to /data/oxford102/experiments/1545100924.6199474/inception_resnet_v2_1545100924.6199474.h5
Epoch 2/100
17/17 [==============================] - 81s 5s/step - loss: 1.2842 - acc: 0.7020 - val_loss: 1.5761 - val_acc: 0.6134

Epoch 00002: val_acc improved from 0.50195 to 0.61337, saving model to /data/oxford102/experiments/1545100924.6199474/inception_resnet_v2_1545100924.6199474.h5
Epoch 3/100
17/17 [==============================] - 74s 4s/step - loss: 0.7966 - acc: 0.8435 - val_loss: 1.3682 - val_acc: 0.6814

Epoch 00003: val_acc improved from 0.61337 to 0.68138, saving model to /data/oxford102/experiments/1545100924.6199474/inception_resnet_v2_1545100924.6199474.h5
Epoch 4/100
17/17 [====================

In [15]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 128,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_3 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_407 (Conv2D)             (None, 127, 127, 32) 864         input_3[0][0]                    
__________________________________________________________________________________________________
batch_normalization_409 (BatchN (None, 127, 127, 32) 96          conv2d_407[0][0]                 
__________________________________________________________________________________________________
activation_407 (Activation)     (None, 127, 127, 32) 0           batch_normalization_409[0][0]    
__________________________________________________________________________________________________
conv2d_408

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
35/35 [==============================] - 90s 3s/step - loss: 2.7810 - acc: 0.3741 - val_loss: 2.0127 - val_acc: 0.5137

Epoch 00001: val_acc improved from -inf to 0.51367, saving model to /data/oxford102/experiments/1545102712.188949/inception_resnet_v2_1545102712.188949.h5
Epoch 2/100
35/35 [==============================] - 82s 2s/step - loss: 1.2956 - acc: 0.7146 - val_loss: 1.5882 - val_acc: 0.6149

Epoch 00002: val_acc improved from 0.51367 to 0.61491, saving model to /data/oxford102/experiments/1545102712.188949/inception_resnet_v2_1545102712.188949.h5
Epoch 3/100
35/35 [==============================] - 79s 2s/step - loss: 0.7901 - acc: 0.8509 - val_loss: 1.3665 - val_acc: 0.6739

Epoch 00003: val_acc improved from 0.61491 to 0.67391, saving model to /data/oxford102/experiments/1545102712.188949/inception_resnet_v2_1545102712.188949.h5
Epoch 4/100
35/35 [==========================

In [16]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 64,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_4 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_610 (Conv2D)             (None, 127, 127, 32) 864         input_4[0][0]                    
__________________________________________________________________________________________________
batch_normalization_613 (BatchN (None, 127, 127, 32) 96          conv2d_610[0][0]                 
__________________________________________________________________________________________________
activation_610 (Activation)     (None, 127, 127, 32) 0           batch_normalization_613[0][0]    
__________________________________________________________________________________________________
conv2d_611

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
71/71 [==============================] - 96s 1s/step - loss: 2.7047 - acc: 0.3939 - val_loss: 2.0130 - val_acc: 0.5377

Epoch 00001: val_acc improved from -inf to 0.53768, saving model to /data/oxford102/experiments/1545104045.7045286/inception_resnet_v2_1545104045.7045286.h5
Epoch 2/100
71/71 [==============================] - 88s 1s/step - loss: 1.3937 - acc: 0.7104 - val_loss: 1.6368 - val_acc: 0.6204

Epoch 00002: val_acc improved from 0.53768 to 0.62039, saving model to /data/oxford102/experiments/1545104045.7045286/inception_resnet_v2_1545104045.7045286.h5
Epoch 3/100
71/71 [==============================] - 87s 1s/step - loss: 0.8712 - acc: 0.8345 - val_loss: 1.3232 - val_acc: 0.6835

Epoch 00003: val_acc improved from 0.62039 to 0.68350, saving model to /data/oxford102/experiments/1545104045.7045286/inception_resnet_v2_1545104045.7045286.h5
Epoch 4/100
71/71 [====================

In [17]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 32,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_5 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_813 (Conv2D)             (None, 127, 127, 32) 864         input_5[0][0]                    
__________________________________________________________________________________________________
batch_normalization_817 (BatchN (None, 127, 127, 32) 96          conv2d_813[0][0]                 
__________________________________________________________________________________________________
activation_813 (Activation)     (None, 127, 127, 32) 0           batch_normalization_817[0][0]    
__________________________________________________________________________________________________
conv2d_814

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
143/143 [==============================] - 105s 735ms/step - loss: 2.8658 - acc: 0.3680 - val_loss: 2.2568 - val_acc: 0.4871

Epoch 00001: val_acc improved from -inf to 0.48713, saving model to /data/oxford102/experiments/1545105650.426833/inception_resnet_v2_1545105650.426833.h5
Epoch 2/100
143/143 [==============================] - 98s 684ms/step - loss: 1.6053 - acc: 0.6481 - val_loss: 1.6935 - val_acc: 0.5951

Epoch 00002: val_acc improved from 0.48713 to 0.59510, saving model to /data/oxford102/experiments/1545105650.426833/inception_resnet_v2_1545105650.426833.h5
Epoch 3/100
143/143 [==============================] - 98s 688ms/step - loss: 1.0455 - acc: 0.7893 - val_loss: 1.4787 - val_acc: 0.6422

Epoch 00003: val_acc improved from 0.59510 to 0.64218, saving model to /data/oxford102/experiments/1545105650.426833/inception_resnet_v2_1545105650.426833.h5
Epoch 4/100
143/143 [========

In [18]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 16,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_6 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_1016 (Conv2D)            (None, 127, 127, 32) 864         input_6[0][0]                    
__________________________________________________________________________________________________
batch_normalization_1021 (Batch (None, 127, 127, 32) 96          conv2d_1016[0][0]                
__________________________________________________________________________________________________
activation_1016 (Activation)    (None, 127, 127, 32) 0           batch_normalization_1021[0][0]   
__________________________________________________________________________________________________
conv2d_101

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
287/287 [==============================] - 126s 439ms/step - loss: 3.0857 - acc: 0.3341 - val_loss: 2.6159 - val_acc: 0.4265

Epoch 00001: val_acc improved from -inf to 0.42647, saving model to /data/oxford102/experiments/1545107391.954375/inception_resnet_v2_1545107391.954375.h5
Epoch 2/100
287/287 [==============================] - 119s 415ms/step - loss: 2.0246 - acc: 0.5698 - val_loss: 2.0688 - val_acc: 0.5371

Epoch 00002: val_acc improved from 0.42647 to 0.53711, saving model to /data/oxford102/experiments/1545107391.954375/inception_resnet_v2_1545107391.954375.h5
Epoch 3/100
287/287 [==============================] - 119s 416ms/step - loss: 1.5126 - acc: 0.6742 - val_loss: 1.8192 - val_acc: 0.5909

Epoch 00003: val_acc improved from 0.53711 to 0.59091, saving model to /data/oxford102/experiments/1545107391.954375/inception_resnet_v2_1545107391.954375.h5
Epoch 4/100
287/287 [======

In [19]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 8,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_7 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_1219 (Conv2D)            (None, 127, 127, 32) 864         input_7[0][0]                    
__________________________________________________________________________________________________
batch_normalization_1225 (Batch (None, 127, 127, 32) 96          conv2d_1219[0][0]                
__________________________________________________________________________________________________
activation_1219 (Activation)    (None, 127, 127, 32) 0           batch_normalization_1225[0][0]   
__________________________________________________________________________________________________
conv2d_122

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
575/575 [==============================] - 163s 283ms/step - loss: 3.5114 - acc: 0.2611 - val_loss: 3.1176 - val_acc: 0.3410

Epoch 00001: val_acc improved from -inf to 0.34099, saving model to /data/oxford102/experiments/1545109745.7254472/inception_resnet_v2_1545109745.7254472.h5
Epoch 2/100
575/575 [==============================] - 156s 271ms/step - loss: 2.7649 - acc: 0.4157 - val_loss: 2.7685 - val_acc: 0.4282

Epoch 00002: val_acc improved from 0.34099 to 0.42818, saving model to /data/oxford102/experiments/1545109745.7254472/inception_resnet_v2_1545109745.7254472.h5
Epoch 3/100
575/575 [==============================] - 156s 272ms/step - loss: 2.3784 - acc: 0.5020 - val_loss: 2.5533 - val_acc: 0.4411

Epoch 00003: val_acc improved from 0.42818 to 0.44107, saving model to /data/oxford102/experiments/1545109745.7254472/inception_resnet_v2_1545109745.7254472.h5
Epoch 4/100
575/575 [

# SGD

In [21]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.9, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 256,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_8 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_1422 (Conv2D)            (None, 127, 127, 32) 864         input_8[0][0]                    
__________________________________________________________________________________________________
batch_normalization_1429 (Batch (None, 127, 127, 32) 96          conv2d_1422[0][0]                
__________________________________________________________________________________________________
activation_1422 (Activation)    (None, 127, 127, 32) 0           batch_normalization_1429[0][0]   
__________________________________________________________________________________________________
conv2d_142

Total params: 111,069,510
Trainable params: 56,730,726
Non-trainable params: 54,338,784
__________________________________________________________________________________________________
Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 86s 5s/step - loss: 3.3373 - acc: 0.2654 - val_loss: 2.3692 - val_acc: 0.4297

Epoch 00001: val_acc improved from -inf to 0.42969, saving model to /data/oxford102/experiments/1545136890.5101461/inception_resnet_v2_1545136890.5101461.h5
Epoch 2/100
17/17 [==============================] - 75s 4s/step - loss: 1.6233 - acc: 0.6077 - val_loss: 1.7177 - val_acc: 0.5800

Epoch 00002: val_acc improved from 0.42969 to 0.57995, saving model to /data/oxford102/experiments/1545136890.5101461/inception_resnet_v2_1545136890.5101461.h5
Epoch 3/100
17/17 [==============================] - 75s 4s/step - loss: 0.9855 - acc: 0.7780 - val_loss: 1.4433 - val_acc: 0.6432

Epoch 00003:

In [22]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.9, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 128,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_9 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_1625 (Conv2D)            (None, 127, 127, 32) 864         input_9[0][0]                    
__________________________________________________________________________________________________
batch_normalization_1633 (Batch (None, 127, 127, 32) 96          conv2d_1625[0][0]                
__________________________________________________________________________________________________
activation_1625 (Activation)    (None, 127, 127, 32) 0           batch_normalization_1633[0][0]   
__________________________________________________________________________________________________
conv2d_162

Total params: 111,069,510
Trainable params: 56,730,726
Non-trainable params: 54,338,784
__________________________________________________________________________________________________
Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
35/35 [==============================] - 92s 3s/step - loss: 2.9695 - acc: 0.3295 - val_loss: 2.0891 - val_acc: 0.4863

Epoch 00001: val_acc improved from -inf to 0.48633, saving model to /data/oxford102/experiments/1545139627.81609/inception_resnet_v2_1545139627.81609.h5
Epoch 2/100
35/35 [==============================] - 80s 2s/step - loss: 1.4069 - acc: 0.6581 - val_loss: 1.5320 - val_acc: 0.6294

Epoch 00002: val_acc improved from 0.48633 to 0.62940, saving model to /data/oxford102/experiments/1545139627.81609/inception_resnet_v2_1545139627.81609.h5
Epoch 3/100
35/35 [==============================] - 81s 2s/step - loss: 0.8705 - acc: 0.7971 - val_loss: 1.2603 - val_acc: 0.6874

Epoch 00003: val_acc

In [23]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.9, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 64,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_10 (InputLayer)           (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_1828 (Conv2D)            (None, 127, 127, 32) 864         input_10[0][0]                   
__________________________________________________________________________________________________
batch_normalization_1837 (Batch (None, 127, 127, 32) 96          conv2d_1828[0][0]                
__________________________________________________________________________________________________
activation_1828 (Activation)    (None, 127, 127, 32) 0           batch_normalization_1837[0][0]   
__________________________________________________________________________________________________
conv2d_182

__________________________________________________________________________________________________
activation_1999 (Activation)    (None, 6, 6, 192)    0           batch_normalization_2008[0][0]   
__________________________________________________________________________________________________
activation_2002 (Activation)    (None, 6, 6, 256)    0           batch_normalization_2011[0][0]   
__________________________________________________________________________________________________
block8_3_mixed (Concatenate)    (None, 6, 6, 448)    0           activation_1999[0][0]            
                                                                 activation_2002[0][0]            
__________________________________________________________________________________________________
block8_3_conv (Conv2D)          (None, 6, 6, 2080)   933920      block8_3_mixed[0][0]             
__________________________________________________________________________________________________
block8_3 (

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
71/71 [==============================] - 98s 1s/step - loss: 2.8970 - acc: 0.3356 - val_loss: 2.0948 - val_acc: 0.4807

Epoch 00001: val_acc improved from -inf to 0.48070, saving model to /data/oxford102/experiments/1545142419.7855225/inception_resnet_v2_1545142419.7855225.h5
Epoch 2/100
71/71 [==============================] - 88s 1s/step - loss: 1.4806 - acc: 0.6362 - val_loss: 1.6758 - val_acc: 0.5680

Epoch 00002: val_acc improved from 0.48070 to 0.56796, saving model to /data/oxford102/experiments/1545142419.7855225/inception_resnet_v2_1545142419.7855225.h5
Epoch 3/100
71/71 [==============================] - 88s 1s/step - loss: 1.0286 - acc: 0.7590 - val_loss: 1.4406 - val_acc: 0.6243

Epoch 00003: val_acc improved from 0.56796 to 0.62427, saving model to /data/oxford102/experiments/1545142419.7855225/inception_resnet_v2_1545142419.7855225.h5
Epoch 4/100
71/71 [====================

In [24]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.9, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 32,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_11 (InputLayer)           (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_2031 (Conv2D)            (None, 127, 127, 32) 864         input_11[0][0]                   
__________________________________________________________________________________________________
batch_normalization_2041 (Batch (None, 127, 127, 32) 96          conv2d_2031[0][0]                
__________________________________________________________________________________________________
activation_2031 (Activation)    (None, 127, 127, 32) 0           batch_normalization_2041[0][0]   
__________________________________________________________________________________________________
conv2d_203

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
143/143 [==============================] - 108s 758ms/step - loss: 2.9583 - acc: 0.3140 - val_loss: 2.2570 - val_acc: 0.4320

Epoch 00001: val_acc improved from -inf to 0.43199, saving model to /data/oxford102/experiments/1545146219.344922/inception_resnet_v2_1545146219.344922.h5
Epoch 2/100
143/143 [==============================] - 99s 689ms/step - loss: 1.7221 - acc: 0.5611 - val_loss: 1.9309 - val_acc: 0.5009

Epoch 00002: val_acc improved from 0.43199 to 0.50094, saving model to /data/oxford102/experiments/1545146219.344922/inception_resnet_v2_1545146219.344922.h5
Epoch 3/100
143/143 [==============================] - 98s 684ms/step - loss: 1.4276 - acc: 0.6421 - val_loss: 1.7872 - val_acc: 0.5301

Epoch 00003: val_acc improved from 0.50094 to 0.53013, saving model to /data/oxford102/experiments/1545146219.344922/inception_resnet_v2_1545146219.344922.h5
Epoch 4/100
143/143 [========

In [25]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.9, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 16,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_12 (InputLayer)           (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_2234 (Conv2D)            (None, 127, 127, 32) 864         input_12[0][0]                   
__________________________________________________________________________________________________
batch_normalization_2245 (Batch (None, 127, 127, 32) 96          conv2d_2234[0][0]                
__________________________________________________________________________________________________
activation_2234 (Activation)    (None, 127, 127, 32) 0           batch_normalization_2245[0][0]   
__________________________________________________________________________________________________
conv2d_223

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
287/287 [==============================] - 127s 443ms/step - loss: 3.1368 - acc: 0.2655 - val_loss: 2.6137 - val_acc: 0.3355

Epoch 00001: val_acc improved from -inf to 0.33548, saving model to /data/oxford102/experiments/1545148489.372287/inception_resnet_v2_1545148489.372287.h5
Epoch 2/100
287/287 [==============================] - 118s 410ms/step - loss: 2.3317 - acc: 0.4012 - val_loss: 2.4211 - val_acc: 0.3720

Epoch 00002: val_acc improved from 0.33548 to 0.37199, saving model to /data/oxford102/experiments/1545148489.372287/inception_resnet_v2_1545148489.372287.h5
Epoch 3/100
287/287 [==============================] - 118s 411ms/step - loss: 2.2449 - acc: 0.4215 - val_loss: 2.4361 - val_acc: 0.3720

Epoch 00003: val_acc did not improve from 0.37199
Epoch 4/100
287/287 [==============================] - 117s 408ms/step - loss: 2.2479 - acc: 0.4014 - val_loss: 2.5018 - val_acc: 0.371

In [26]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.9, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 8,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_13 (InputLayer)           (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_2437 (Conv2D)            (None, 127, 127, 32) 864         input_13[0][0]                   
__________________________________________________________________________________________________
batch_normalization_2449 (Batch (None, 127, 127, 32) 96          conv2d_2437[0][0]                
__________________________________________________________________________________________________
activation_2437 (Activation)    (None, 127, 127, 32) 0           batch_normalization_2449[0][0]   
__________________________________________________________________________________________________
conv2d_243

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.


FailedPreconditionError: Attempting to use uninitialized value dense_25/bias
	 [[{{node dense_25/bias/_114256}} = _Send[T=DT_FLOAT, client_terminated=false, recv_device="/job:localhost/replica:0/task:0/device:CPU:0", send_device="/job:localhost/replica:0/task:0/device:GPU:0", send_device_incarnation=1, tensor_name="edge_6_dense_25/bias", _device="/job:localhost/replica:0/task:0/device:GPU:0"](dense_25/bias)]]

In [ ]:
print("Done")

In [11]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.9, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 128,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

In [11]:
for network in ['inception_resnet_v2', 'vgg16', 'vgg19', 'mobilenet_v2']:
    for lr in [0.1, 0.01, 0.001]:
        for momentum in [0.5, 0.75, 0.9]:
            for decay in [0.01, 0.1, 0.2]:
                for nesterov in [True, False]:
                    _optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
                    params['optimizer'] = _optimizer
                    _model, input_processor = get_model(params["network_name"])
                    train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
                    train_model(params, _model, (train_generator, validation_generator))

In [ ]:
print("DONE")

In [ ]:
lr=0.001
momentum = 0.9
decay = 0.1
nesterov = False
_optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
params['optimizer'] = _optimizer
_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

In [12]:
import itertools
import numpy

In [13]:
lr = [0.1, 0.01, 0.001]
momentum = [0.5, 0.75, 0.9]
nesterov = [True, False]
decay = [0.001, 0.01, 0.1, 0.2]


In [14]:
grid = list(itertools.product(lr, momentum, nesterov, decay))

In [14]:
grid

[(0.1, 0.5, True, 0.001),
 (0.1, 0.5, True, 0.01),
 (0.1, 0.5, True, 0.1),
 (0.1, 0.5, True, 0.2),
 (0.1, 0.5, False, 0.001),
 (0.1, 0.5, False, 0.01),
 (0.1, 0.5, False, 0.1),
 (0.1, 0.5, False, 0.2),
 (0.1, 0.75, True, 0.001),
 (0.1, 0.75, True, 0.01),
 (0.1, 0.75, True, 0.1),
 (0.1, 0.75, True, 0.2),
 (0.1, 0.75, False, 0.001),
 (0.1, 0.75, False, 0.01),
 (0.1, 0.75, False, 0.1),
 (0.1, 0.75, False, 0.2),
 (0.1, 0.9, True, 0.001),
 (0.1, 0.9, True, 0.01),
 (0.1, 0.9, True, 0.1),
 (0.1, 0.9, True, 0.2),
 (0.1, 0.9, False, 0.001),
 (0.1, 0.9, False, 0.01),
 (0.1, 0.9, False, 0.1),
 (0.1, 0.9, False, 0.2),
 (0.01, 0.5, True, 0.001),
 (0.01, 0.5, True, 0.01),
 (0.01, 0.5, True, 0.1),
 (0.01, 0.5, True, 0.2),
 (0.01, 0.5, False, 0.001),
 (0.01, 0.5, False, 0.01),
 (0.01, 0.5, False, 0.1),
 (0.01, 0.5, False, 0.2),
 (0.01, 0.75, True, 0.001),
 (0.01, 0.75, True, 0.01),
 (0.01, 0.75, True, 0.1),
 (0.01, 0.75, True, 0.2),
 (0.01, 0.75, False, 0.001),
 (0.01, 0.75, False, 0.01),
 (0.01, 0.75

In [26]:
choices = numpy.random.choice(range(len(grid)), int(len(grid)*0.2), replace=False)

In [47]:
choices = [1, 11, 15, 22, 25, 28, 30, 32, 36, 40, 44, 60, 66, 68]

In [48]:
params = {'network_name': "inception_resnet_v2",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.9, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 128,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

In [29]:
for i in grid:
    print(i)
    lr, momentum, nesterov, decay = i
    _optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
    params['optimizer'] = _optimizer
    _model, input_processor = get_model(params["network_name"])
    train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
    train_model(params, _model, (train_generator, validation_generator))

(0.1, 0.5, True, 0.001)


/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_4 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_610 (Conv2D)             (None, 127, 127, 32) 864         input_4[0][0]                    
__________________________________________________________________________________________________
batch_normalization_611 (BatchN (None, 127, 127, 32) 96          conv2d_610[0][0]                 
__________________________________________________________________________________________________
activation_610 (Activation)     (None, 127, 127, 32) 0           batch_normalization_611[0][0]    
__________________________________________________________________________________________________
conv2d_611

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
575/575 [==============================] - 156s 271ms/step - loss: 3.8383 - acc: 0.1628 - val_loss: 3.2912 - val_acc: 0.2270

Epoch 00001: val_acc improved from -inf to 0.22702, saving model to /data/oxford102/experiments/1545504950.1968458/inception_resnet_v2_1545504950.1968458.h5
Epoch 2/100
575/575 [==============================] - 149s 260ms/step - loss: 3.0400 - acc: 0.2604 - val_loss: 3.1930 - val_acc: 0.2238

Epoch 00002: val_acc did not improve from 0.22702
Epoch 3/100
575/575 [==============================] - 150s 260ms/step - loss: 2.9611 - acc: 0.2622 - val_loss: 3.0108 - val_acc: 0.2477

Epoch 00003: val_acc improved from 0.22702 to 0.24770, saving model to /data/oxford102/experiments/1545504950.1968458/inception_resnet_v2_1545504950.1968458.h5
Epoch 4/100
575/575 [==============================] - 150s 260ms/step - loss: 2.9486 - acc: 0.2557 - val_loss: 2.9599 - val_acc: 0

                                                                 activation_964[0][0]             
__________________________________________________________________________________________________
block17_19_conv (Conv2D)        (None, 14, 14, 1088) 418880      block17_19_mixed[0][0]           
__________________________________________________________________________________________________
block17_19 (Lambda)             (None, 14, 14, 1088) 0           block17_18_ac[0][0]              
                                                                 block17_19_conv[0][0]            
__________________________________________________________________________________________________
block17_19_ac (Activation)      (None, 14, 14, 1088) 0           block17_19[0][0]                 
__________________________________________________________________________________________________
conv2d_966 (Conv2D)             (None, 14, 14, 128)  139264      block17_19_ac[0][0]              
__________

...

conv2d_2425 (Conv2D)            (None, 6, 6, 192)    399360      block8_7_ac[0][0]                
__________________________________________________________________________________________________
conv2d_2428 (Conv2D)            (None, 6, 6, 256)    172032      activation_2427[0][0]            
__________________________________________________________________________________________________
batch_normalization_2434 (Batch (None, 6, 6, 192)    576         conv2d_2425[0][0]                
__________________________________________________________________________________________________
batch_normalization_2437 (Batch (None, 6, 6, 256)    768         conv2d_2428[0][0]                
__________________________________________________________________________________________________
activation_2425 (Activation)    (None, 6, 6, 192)    0           batch_normalization_2434[0][0]   
__________________________________________________________________________________________________
activation

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
575/575 [==============================] - 168s 293ms/step - loss: 4.0144 - acc: 0.1654 - val_loss: 3.1310 - val_acc: 0.2399

Epoch 00001: val_acc improved from -inf to 0.23989, saving model to /data/oxford102/experiments/1545528403.266252/inception_resnet_v2_1545528403.266252.h5
Epoch 2/100
575/575 [==============================] - 158s 275ms/step - loss: 2.9238 - acc: 0.2767 - val_loss: 3.0496 - val_acc: 0.2459

Epoch 00002: val_acc improved from 0.23989 to 0.24586, saving model to /data/oxford102/experiments/1545528403.266252/inception_resnet_v2_1545528403.266252.h5
Epoch 3/100
575/575 [==============================] - 159s 277ms/step - loss: 2.9051 - acc: 0.2748 - val_loss: 3.0735 - val_acc: 0.2376

Epoch 00003: val_acc did not improve from 0.24586
Epoch 4/100
575/575 [==============================] - 159s 277ms/step - loss: 2.8314 - acc: 0.2804 - val_loss: 2.9110 - val_acc: 0.259

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
575/575 [==============================] - 170s 296ms/step - loss: 4.0085 - acc: 0.1693 - val_loss: 3.1523 - val_acc: 0.2390

Epoch 00001: val_acc improved from -inf to 0.23897, saving model to /data/oxford102/experiments/1545531032.190229/inception_resnet_v2_1545531032.190229.h5
Epoch 2/100
575/575 [==============================] - 160s 279ms/step - loss: 2.8658 - acc: 0.2937 - val_loss: 2.9300 - val_acc: 0.2762

Epoch 00002: val_acc improved from 0.23897 to 0.27624, saving model to /data/oxford102/experiments/1545531032.190229/inception_resnet_v2_1545531032.190229.h5
Epoch 3/100
575/575 [==============================] - 161s 280ms/step - loss: 2.7166 - acc: 0.3159 - val_loss: 2.8522 - val_acc: 0.2744

Epoch 00003: val_acc did not improve from 0.27624
Epoch 4/100
575/575 [==============================] - 161s 280ms/step - loss: 2.6931 - acc: 0.3150 - val_loss: 2.9108 - val_acc: 0.269

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.


KeyboardInterrupt: 

In [ ]:
choices = [1, 11, 15, 22, 25, 28, 30, 32, 36, 40, 44, 60, 66, 68]

In [ ]:
for i in choices:
    print(i, grid[i])
    lr, momentum, nesterov, decay = grid[i]
    _optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
    params['optimizer'] = _optimizer
    _model, input_processor = get_model(params["network_name"])
    train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
    train_model(params, _model, (train_generator, validation_generator))

In [ ]:
for i in choices:
    print(i, grid[i])
    lr, momentum, nesterov, decay = grid[i]
    _optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
    params['optimizer'] = _optimizer
    _model, input_processor = get_model(params["network_name"])
    train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
    train_model(params, _model, (train_generator, validation_generator))

# VGG19

In [ ]:
choices = [1, 11, 15, 22, 25, 28, 30, 32, 36, 40, 44, 60, 66, 68]

In [9]:
params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.9, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 128,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

In [49]:
for i in choices:
    print("params combination: ", i, grid[i])
    lr, momentum, nesterov, decay = grid[i]
    _optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
    params['optimizer'] = _optimizer
    _model, input_processor = get_model(params["network_name"])
    train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
    train_model(params, _model, (train_generator, validation_generator))

1 (0.1, 0.5, True, 0.01)


/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_6 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_610 (Conv2D)             (None, 127, 127, 32) 864         input_6[0][0]                    
__________________________________________________________________________________________________
batch_normalization_615 (BatchN (None, 127, 127, 32) 96          conv2d_610[0][0]                 
__________________________________________________________________________________________________
activation_610 (Activation)     (None, 127, 127, 32) 0           batch_normalization_615[0][0]    
__________________________________________________________________________________________________
conv2d_611

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 53s 3s/step - loss: 3.4093 - acc: 0.2454 - val_loss: 2.6379 - val_acc: 0.3730

Epoch 00001: val_acc improved from -inf to 0.37305, saving model to /data/oxford102/experiments/1545963216.2233803/inception_resnet_v2_1545963216.2233803.h5
Epoch 2/100
17/17 [==============================] - 45s 3s/step - loss: 2.4211 - acc: 0.4159 - val_loss: 2.0693 - val_acc: 0.4979

Epoch 00002: val_acc improved from 0.37305 to 0.49793, saving model to /data/oxford102/experiments/1545963216.2233803/inception_resnet_v2_1545963216.2233803.h5
Epoch 3/100
17/17 [==============================] - 46s 3s/step - loss: 1.6786 - acc: 0.5886 - val_loss: 1.8287 - val_acc: 0.5569

Epoch 00003: val_acc improved from 0.49793 to 0.55694, saving model to /data/oxford102/experiments/1545963216.2233803/inception_resnet_v2_1545963216.2233803.h5
Epoch 4/100
17/17 [====================

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 54s 3s/step - loss: 3.6254 - acc: 0.2270 - val_loss: 3.0369 - val_acc: 0.2939

Epoch 00001: val_acc improved from -inf to 0.29395, saving model to /data/oxford102/experiments/1545964600.5470428/inception_resnet_v2_1545964600.5470428.h5
Epoch 2/100
17/17 [==============================] - 46s 3s/step - loss: 2.8363 - acc: 0.3290 - val_loss: 2.6352 - val_acc: 0.3561

Epoch 00002: val_acc improved from 0.29395 to 0.35611, saving model to /data/oxford102/experiments/1545964600.5470428/inception_resnet_v2_1545964600.5470428.h5
Epoch 3/100
17/17 [==============================] - 46s 3s/step - loss: 2.2540 - acc: 0.4448 - val_loss: 2.4724 - val_acc: 0.3965

Epoch 00003: val_acc improved from 0.35611 to 0.39648, saving model to /data/oxford102/experiments/1545964600.5470428/inception_resnet_v2_1545964600.5470428.h5
Epoch 4/100
17/17 [====================

...

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 55s 3s/step - loss: 3.6274 - acc: 0.2160 - val_loss: 3.0082 - val_acc: 0.2969

Epoch 00001: val_acc improved from -inf to 0.29688, saving model to /data/oxford102/experiments/1545967623.946288/inception_resnet_v2_1545967623.946288.h5
Epoch 2/100
17/17 [==============================] - 46s 3s/step - loss: 2.8031 - acc: 0.3226 - val_loss: 2.5362 - val_acc: 0.3613

Epoch 00002: val_acc improved from 0.29688 to 0.36128, saving model to /data/oxford102/experiments/1545967623.946288/inception_resnet_v2_1545967623.946288.h5
Epoch 3/100
17/17 [==============================] - 46s 3s/step - loss: 2.1421 - acc: 0.4337 - val_loss: 2.3935 - val_acc: 0.3841

Epoch 00003: val_acc improved from 0.36128 to 0.38406, saving model to /data/oxford102/experiments/1545967623.946288/inception_resnet_v2_1545967623.946288.h5
Epoch 4/100
17/17 [==========================

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 56s 3s/step - loss: 3.6854 - acc: 0.2123 - val_loss: 2.9088 - val_acc: 0.3281

Epoch 00001: val_acc improved from -inf to 0.32812, saving model to /data/oxford102/experiments/1545969576.2248561/inception_resnet_v2_1545969576.2248561.h5
Epoch 2/100
17/17 [==============================] - 45s 3s/step - loss: 2.6469 - acc: 0.3773 - val_loss: 2.3638 - val_acc: 0.4379

Epoch 00002: val_acc improved from 0.32812 to 0.43789, saving model to /data/oxford102/experiments/1545969576.2248561/inception_resnet_v2_1545969576.2248561.h5
Epoch 3/100
17/17 [==============================] - 46s 3s/step - loss: 1.7979 - acc: 0.5887 - val_loss: 2.1167 - val_acc: 0.4979

Epoch 00003: val_acc improved from 0.43789 to 0.49793, saving model to /data/oxford102/experiments/1545969576.2248561/inception_resnet_v2_1545969576.2248561.h5
Epoch 4/100
17/17 [====================

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 56s 3s/step - loss: 3.7359 - acc: 0.2165 - val_loss: 2.9251 - val_acc: 0.3223

Epoch 00001: val_acc improved from -inf to 0.32227, saving model to /data/oxford102/experiments/1545971455.7233753/inception_resnet_v2_1545971455.7233753.h5
Epoch 2/100
17/17 [==============================] - 45s 3s/step - loss: 2.6459 - acc: 0.3796 - val_loss: 2.3543 - val_acc: 0.4565

Epoch 00002: val_acc improved from 0.32227 to 0.45652, saving model to /data/oxford102/experiments/1545971455.7233753/inception_resnet_v2_1545971455.7233753.h5
Epoch 3/100
17/17 [==============================] - 46s 3s/step - loss: 1.7811 - acc: 0.5928 - val_loss: 2.1194 - val_acc: 0.4793

Epoch 00003: val_acc improved from 0.45652 to 0.47930, saving model to /data/oxford102/experiments/1545971455.7233753/inception_resnet_v2_1545971455.7233753.h5
Epoch 4/100
17/17 [====================

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
{'network_name': 'inception_resnet_v2', 'image_aug': False, 'optimizer_name': 'SGD', 'optimizer_params': None, 'batch_size': 128, 'epochs': 100, 'image_size': (256, 256), 'log_time': 1545973466.3386588}


ResourceExhaustedError: OOM when allocating tensor with shape[128,64,125,125] and type float on /job:localhost/replica:0/task:0/device:GPU:0 by allocator GPU_0_bfc
	 [[{{node conv2d_1830/convolution}} = Conv2D[T=DT_FLOAT, data_format="NCHW", dilations=[1, 1, 1, 1], padding="SAME", strides=[1, 1, 1, 1], use_cudnn_on_gpu=true, _device="/job:localhost/replica:0/task:0/device:GPU:0"](activation_1829/Relu, conv2d_1830/kernel/read)]]
Hint: If you want to see a list of allocated tensors when OOM happens, add report_tensor_allocations_upon_oom to RunOptions for current allocation info.

	 [[{{node loss_11/mul/_88393}} = _Recv[client_terminated=false, recv_device="/job:localhost/replica:0/task:0/device:CPU:0", send_device="/job:localhost/replica:0/task:0/device:GPU:0", send_device_incarnation=1, tensor_name="edge_4516_loss_11/mul", tensor_type=DT_FLOAT, _device="/job:localhost/replica:0/task:0/device:CPU:0"]()]]
Hint: If you want to see a list of allocated tensors when OOM happens, add report_t

In [15]:
# run the remaining combinations after OOM above
choices = [30, 32, 36, 40, 44, 60, 66, 68]
for i in choices:
    print(i, grid[i])
    lr, momentum, nesterov, decay = grid[i]
    _optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
    params['optimizer'] = _optimizer
    _model, input_processor = get_model(params["network_name"])
    train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
    train_model(params, _model, (train_generator, validation_generator))

30 (0.01, 0.5, False, 0.1)


/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 54s 3s/step - loss: 4.3933 - acc: 0.1121 - val_loss: 3.5401 - val_acc: 0.2461

Epoch 00001: val_acc improved from -inf to 0.24609, saving model to /data/oxford102/experiments/1546129748.782239/vgg19_1546129748.782239.h5
Epoch 2/100
17/17 [==============================] - 47s 3s/step - loss: 3.3242 - acc: 0.2661 - val_loss: 3.0600 - val_acc: 0.3292

Epoch 00002: val_acc improved from 0.24609 to 0.32919, saving model to /data/oxford102/experiments/1546129748.782239/vgg19_1546129748.782239.h5
Epoch 3/100
17/17 [==============================] - 50s 3s/step - loss: 2.3777 - acc: 0.4818 - val_loss: 2.9061 - val_acc: 0.3623

Epoch 00003: val_acc improved from 0.32919 to 0.36232, saving model to /data/oxford102/experiments/1546129748.782239/vgg19_1546129748.782239.h5
Epoch 4/100
17/17 [==============================] - 41s 2s/step - loss: 2.2525 - acc: 

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 43s 3s/step - loss: 3.6168 - acc: 0.2495 - val_loss: 2.4476 - val_acc: 0.4648

Epoch 00001: val_acc improved from -inf to 0.46484, saving model to /data/oxford102/experiments/1546130554.506069/vgg19_1546130554.506069.h5
Epoch 2/100
17/17 [==============================] - 41s 2s/step - loss: 2.0975 - acc: 0.5193 - val_loss: 1.7171 - val_acc: 0.6180

Epoch 00002: val_acc improved from 0.46484 to 0.61801, saving model to /data/oxford102/experiments/1546130554.506069/vgg19_1546130554.506069.h5
Epoch 3/100
17/17 [==============================] - 41s 2s/step - loss: 0.9454 - acc: 0.8302 - val_loss: 1.4813 - val_acc: 0.6542

Epoch 00003: val_acc improved from 0.61801 to 0.65424, saving model to /data/oxford102/experiments/1546130554.506069/vgg19_1546130554.506069.h5
Epoch 4/100
17/17 [==============================] - 41s 2s/step - loss: 0.7114 - acc: 

Epoch 2/100
17/17 [==============================] - 41s 2s/step - loss: 1.7439 - acc: 0.5795 - val_loss: 1.3992 - val_acc: 0.6646

Epoch 00002: val_acc improved from 0.49609 to 0.66460, saving model to /data/oxford102/experiments/1546131846.683898/vgg19_1546131846.683898.h5
Epoch 3/100
17/17 [==============================] - 41s 2s/step - loss: 0.6729 - acc: 0.8754 - val_loss: 1.1944 - val_acc: 0.7298

Epoch 00003: val_acc improved from 0.66460 to 0.72981, saving model to /data/oxford102/experiments/1546131846.683898/vgg19_1546131846.683898.h5
Epoch 4/100
17/17 [==============================] - 41s 2s/step - loss: 0.4381 - acc: 0.9288 - val_loss: 1.0261 - val_acc: 0.7474

Epoch 00004: val_acc improved from 0.72981 to 0.74741, saving model to /data/oxford102/experiments/1546131846.683898/vgg19_1546131846.683898.h5
Epoch 5/100
17/17 [==============================] - 41s 2s/step - loss: 0.2536 - acc: 0.9700 - val_loss: 0.9484 - val_acc: 0.7681

Epoch 00005: val_acc improved from 0.747

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
 4/17 [======>.......................] - ETA: 26s - loss: 5.5368 - acc: 0.0137{'network_name': 'vgg19', 'image_aug': False, 'optimizer_name': 'SGD', 'optimizer_params': None, 'batch_size': 128, 'epochs': 100, 'image_size': (256, 256), 'log_time': 1546133312.5231066}


ResourceExhaustedError: OOM when allocating tensor with shape[128,64,256,256] and type float on /job:localhost/replica:0/task:0/device:GPU:0 by allocator GPU_0_bfc
	 [[{{node block1_conv2_5/convolution}} = Conv2D[T=DT_FLOAT, data_format="NCHW", dilations=[1, 1, 1, 1], padding="SAME", strides=[1, 1, 1, 1], use_cudnn_on_gpu=true, _device="/job:localhost/replica:0/task:0/device:GPU:0"](block1_conv1_5/Relu, block1_conv2_5/kernel/read)]]
Hint: If you want to see a list of allocated tensors when OOM happens, add report_tensor_allocations_upon_oom to RunOptions for current allocation info.

	 [[{{node loss_5/mul/_2291}} = _Recv[client_terminated=false, recv_device="/job:localhost/replica:0/task:0/device:CPU:0", send_device="/job:localhost/replica:0/task:0/device:GPU:0", send_device_incarnation=1, tensor_name="edge_770_loss_5/mul", tensor_type=DT_FLOAT, _device="/job:localhost/replica:0/task:0/device:CPU:0"]()]]
Hint: If you want to see a list of allocated tensors when OOM happens, add report_

In [17]:
# run the remaining combinations after OOM above
choices = [60, 66, 68]
for i in choices:
    print(i, grid[i])
    lr, momentum, nesterov, decay = grid[i]
    _optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
    params['optimizer'] = _optimizer
    _model, input_processor = get_model(params["network_name"])
    train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
    train_model(params, _model, (train_generator, validation_generator))

60 (0.001, 0.75, False, 0.001)


/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 53s 3s/step - loss: 5.1442 - acc: 0.0161 - val_loss: 4.7406 - val_acc: 0.0469

Epoch 00001: val_acc improved from -inf to 0.04688, saving model to /data/oxford102/experiments/1546136337.554975/vgg19_1546136337.554975.h5
Epoch 2/100
17/17 [==============================] - 47s 3s/step - loss: 4.3777 - acc: 0.0859 - val_loss: 3.9540 - val_acc: 0.1511

Epoch 00002: val_acc improved from 0.04688 to 0.15114, saving model to /data/oxford102/experiments/1546136337.554975/vgg19_1546136337.554975.h5
Epoch 3/100
17/17 [==============================] - 50s 3s/step - loss: 3.4693 - acc: 0.2324 - val_loss: 3.5358 - val_acc: 0.2153

Epoch 00003: val_acc improved from 0.15114 to 0.21532, saving model to /data/oxford102/experiments/1546136337.554975/vgg19_1546136337.554975.h5
Epoch 4/100
17/17 [==============================] - 41s 2s/step - loss: 2.9745 - acc: 

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 43s 3s/step - loss: 5.1367 - acc: 0.0244 - val_loss: 4.5791 - val_acc: 0.0635

Epoch 00001: val_acc improved from -inf to 0.06348, saving model to /data/oxford102/experiments/1546137620.624658/vgg19_1546137620.624658.h5
Epoch 2/100
17/17 [==============================] - 41s 2s/step - loss: 4.2620 - acc: 0.1075 - val_loss: 4.0157 - val_acc: 0.1605

Epoch 00002: val_acc improved from 0.06348 to 0.16046, saving model to /data/oxford102/experiments/1546137620.624658/vgg19_1546137620.624658.h5
Epoch 3/100
17/17 [==============================] - 41s 2s/step - loss: 3.4305 - acc: 0.2490 - val_loss: 3.6785 - val_acc: 0.1988

Epoch 00003: val_acc improved from 0.16046 to 0.19876, saving model to /data/oxford102/experiments/1546137620.624658/vgg19_1546137620.624658.h5
Epoch 4/100
17/17 [==============================] - 41s 2s/step - loss: 3.1535 - acc: 


Epoch 00015: val_acc improved from 0.67288 to 0.67495, saving model to /data/oxford102/experiments/1546138355.3299742/vgg19_1546138355.3299742.h5
Epoch 16/100
17/17 [==============================] - 41s 2s/step - loss: 0.3044 - acc: 0.9812 - val_loss: 1.4239 - val_acc: 0.6874

Epoch 00016: val_acc improved from 0.67495 to 0.68737, saving model to /data/oxford102/experiments/1546138355.3299742/vgg19_1546138355.3299742.h5
Epoch 17/100
17/17 [==============================] - 41s 2s/step - loss: 0.2829 - acc: 0.9867 - val_loss: 1.5413 - val_acc: 0.6573

Epoch 00017: val_acc did not improve from 0.68737
Epoch 18/100
17/17 [==============================] - 41s 2s/step - loss: 0.2509 - acc: 0.9867 - val_loss: 1.4329 - val_acc: 0.6656

Epoch 00018: val_acc did not improve from 0.68737
Epoch 19/100
17/17 [==============================] - 42s 2s/step - loss: 0.2343 - acc: 0.9917 - val_loss: 1.3788 - val_acc: 0.6934

Epoch 00019: val_acc improved from 0.68737 to 0.69336, saving model to /dat

# mobilenet_v2

In [14]:
params = {'network_name': "mobilenet_v2",
         'image_aug': False,
         'optimizer_name': "SGD", 
         'optimizer': optimizers.SGD(lr=0.01, momentum=0.9, decay=0.0, nesterov=False),
         'optimizer_params': None, 
         'batch_size': 128,
         'epochs': 100,
         'image_size': (224, 224),
         'log_time': None}

In [24]:
choices = [1, 11, 15, 22, 25, 28, 30, 32, 36, 40, 44, 60, 66, 68]
for i in choices:
    print(i, grid[i])
    lr, momentum, nesterov, decay = grid[i]
    _optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
    params['optimizer'] = _optimizer
    _model, input_processor = get_model(params["network_name"], image_size=params["image_size"])
    train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
    train_model(params, _model, (train_generator, validation_generator))

1 (0.1, 0.5, True, 0.01)
9412608/9406464 [==============================] - 0s 0us/step


/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 17s 993ms/step - loss: 2.7103 - acc: 0.4136 - val_loss: 1.8266 - val_acc: 0.5850

Epoch 00001: val_acc improved from -inf to 0.58496, saving model to /data/oxford102/experiments/1546139759.7948604/mobilenet_v2_1546139759.7948604.h5
Epoch 2/100
17/17 [==============================] - 9s 539ms/step - loss: 1.4253 - acc: 0.6742 - val_loss: 1.2152 - val_acc: 0.7122

Epoch 00002: val_acc improved from 0.58496 to 0.71222, saving model to /data/oxford102/experiments/1546139759.7948604/mobilenet_v2_1546139759.7948604.h5
Epoch 3/100
17/17 [==============================] - 13s 746ms/step - loss: 0.6177 - acc: 0.8874 - val_loss: 0.9360 - val_acc: 0.7785

Epoch 00003: val_acc improved from 0.71222 to 0.77847, saving model to /data/oxford102/experiments/1546139759.7948604/mobilenet_v2_1546139759.7948604.h5
Epoch 4/100
17/17 [==============================] -

17/17 [==============================] - 13s 750ms/step - loss: 0.4535 - acc: 0.9404 - val_loss: 1.1685 - val_acc: 0.7205

Epoch 00005: val_acc did not improve from 0.73602
Epoch 6/100
17/17 [==============================] - 14s 822ms/step - loss: 0.4030 - acc: 0.9490 - val_loss: 1.1220 - val_acc: 0.7433

Epoch 00006: val_acc improved from 0.73602 to 0.74327, saving model to /data/oxford102/experiments/1546140792.6023417/mobilenet_v2_1546140792.6023417.h5
Epoch 7/100
17/17 [==============================] - 14s 796ms/step - loss: 0.3001 - acc: 0.9756 - val_loss: 1.0548 - val_acc: 0.7619

Epoch 00007: val_acc improved from 0.74327 to 0.76190, saving model to /data/oxford102/experiments/1546140792.6023417/mobilenet_v2_1546140792.6023417.h5
Epoch 8/100
17/17 [==============================] - 13s 778ms/step - loss: 0.2577 - acc: 0.9821 - val_loss: 1.0487 - val_acc: 0.7629

Epoch 00008: val_acc improved from 0.76190 to 0.76294, saving model to /data/oxford102/experiments/1546140792.602341

{'network_name': 'mobilenet_v2', 'image_aug': False, 'optimizer_name': 'SGD', 'optimizer_params': None, 'batch_size': 128, 'epochs': 100, 'image_size': (224, 224), 'log_time': 1546141140.2198877}
30 (0.01, 0.5, False, 0.1)
Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 17s 990ms/step - loss: 3.6146 - acc: 0.2514 - val_loss: 2.6806 - val_acc: 0.4131

Epoch 00001: val_acc improved from -inf to 0.41309, saving model to /data/oxford102/experiments/1546141499.6975868/mobilenet_v2_1546141499.6975868.h5
Epoch 2/100
17/17 [==============================] - 9s 504ms/step - loss: 2.3992 - acc: 0.4674 - val_loss: 2.1456 - val_acc: 0.4979

Epoch 00002: val_acc improved from 0.41309 to 0.49793, saving model to /data/oxford102/experiments/1546141499.6975868/mobilenet_v2_1546141499.6975868.h5
Epoch 3/100
17/17 [==============================] - 12s 723ms/step - loss: 1.4371 - acc: 0.7006 - val_loss: 1.9463 -

Epoch 13/100
17/17 [==============================] - 13s 774ms/step - loss: 0.0491 - acc: 0.9995 - val_loss: 0.6966 - val_acc: 0.8313

Epoch 00013: val_acc did not improve from 0.83437
Epoch 14/100
17/17 [==============================] - 13s 766ms/step - loss: 0.0402 - acc: 1.0000 - val_loss: 0.7488 - val_acc: 0.8002

Epoch 00014: val_acc did not improve from 0.83437
Epoch 15/100
17/17 [==============================] - 13s 756ms/step - loss: 0.0397 - acc: 0.9995 - val_loss: 0.7468 - val_acc: 0.8302

Epoch 00015: val_acc did not improve from 0.83437
Epoch 00015: early stopping
{'network_name': 'mobilenet_v2', 'image_aug': False, 'optimizer_name': 'SGD', 'optimizer_params': None, 'batch_size': 128, 'epochs': 100, 'image_size': (224, 224), 'log_time': 1546141881.4786265}
36 (0.01, 0.75, False, 0.001)
Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
15/17 [=========================>....] - ETA: 1s - loss: 3.3318 - acc: 0.3057{'network_n

ResourceExhaustedError: OOM when allocating tensor with shape[12288,113,113] and type float on /job:localhost/replica:0/task:0/device:GPU:0 by allocator GPU_0_bfc
	 [[{{node block_1_pad_8/Pad}} = Pad[T=DT_FLOAT, Tpaddings=DT_INT32, _device="/job:localhost/replica:0/task:0/device:GPU:0"](block_1_expand_relu_8/Relu6, block_1_pad_8/Pad-1-LayoutOptimizer)]]
Hint: If you want to see a list of allocated tensors when OOM happens, add report_tensor_allocations_upon_oom to RunOptions for current allocation info.

	 [[{{node metrics_11/acc/Mean/_24665}} = _Recv[client_terminated=false, recv_device="/job:localhost/replica:0/task:0/device:CPU:0", send_device="/job:localhost/replica:0/task:0/device:GPU:0", send_device_incarnation=1, tensor_name="edge_1574_metrics_11/acc/Mean", tensor_type=DT_FLOAT, _device="/job:localhost/replica:0/task:0/device:CPU:0"]()]]
Hint: If you want to see a list of allocated tensors when OOM happens, add report_tensor_allocations_upon_oom to RunOptions for current allocat

In [15]:
choices = [36, 40, 44, 60, 66, 68]
for i in choices:
    print(i, grid[i])
    lr, momentum, nesterov, decay = grid[i]
    _optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
    params['optimizer'] = _optimizer
    _model, input_processor = get_model(params["network_name"], image_size=params["image_size"])
    train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
    train_model(params, _model, (train_generator, validation_generator))

36 (0.01, 0.75, False, 0.001)


/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 18s 1s/step - loss: 3.1052 - acc: 0.3410 - val_loss: 1.9490 - val_acc: 0.5479

Epoch 00001: val_acc improved from -inf to 0.54785, saving model to /data/oxford102/experiments/1546143378.7641072/mobilenet_v2_1546143378.7641072.h5
Epoch 2/100
17/17 [==============================] - 9s 533ms/step - loss: 1.5740 - acc: 0.6342 - val_loss: 1.2807 - val_acc: 0.7019

Epoch 00002: val_acc improved from 0.54785 to 0.70186, saving model to /data/oxford102/experiments/1546143378.7641072/mobilenet_v2_1546143378.7641072.h5
Epoch 3/100
17/17 [==============================] - 13s 740ms/step - loss: 0.6023 - acc: 0.8957 - val_loss: 1.1068 - val_acc: 0.7412

Epoch 00003: val_acc improved from 0.70186 to 0.74120, saving model to /data/oxford102/experiments/1546143378.7641072/mobilenet_v2_1546143378.7641072.h5
Epoch 4/100
17/17 [==============================] - 14

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 17s 1s/step - loss: 2.9381 - acc: 0.3704 - val_loss: 1.8290 - val_acc: 0.5654

Epoch 00001: val_acc improved from -inf to 0.56543, saving model to /data/oxford102/experiments/1546143606.4002857/mobilenet_v2_1546143606.4002857.h5
Epoch 2/100
17/17 [==============================] - 9s 501ms/step - loss: 1.4442 - acc: 0.6613 - val_loss: 1.1587 - val_acc: 0.7215

Epoch 00002: val_acc improved from 0.56543 to 0.72153, saving model to /data/oxford102/experiments/1546143606.4002857/mobilenet_v2_1546143606.4002857.h5
Epoch 3/100
17/17 [==============================] - 13s 766ms/step - loss: 0.5788 - acc: 0.8906 - val_loss: 0.9297 - val_acc: 0.7743

Epoch 00003: val_acc improved from 0.72153 to 0.77433, saving model to /data/oxford102/experiments/1546143606.4002857/mobilenet_v2_1546143606.4002857.h5
Epoch 4/100
17/17 [==============================] - 13

Epoch 12/100
17/17 [==============================] - 12s 705ms/step - loss: 0.0422 - acc: 0.9995 - val_loss: 0.5959 - val_acc: 0.8520

Epoch 00012: val_acc improved from 0.84886 to 0.85197, saving model to /data/oxford102/experiments/1546143969.900804/mobilenet_v2_1546143969.900804.h5
Epoch 13/100
17/17 [==============================] - 14s 812ms/step - loss: 0.0390 - acc: 0.9995 - val_loss: 0.6036 - val_acc: 0.8478

Epoch 00013: val_acc did not improve from 0.85197
Epoch 14/100
17/17 [==============================] - 13s 754ms/step - loss: 0.0318 - acc: 0.9995 - val_loss: 0.6306 - val_acc: 0.8385

Epoch 00014: val_acc did not improve from 0.85197
Epoch 15/100
17/17 [==============================] - 13s 756ms/step - loss: 0.0308 - acc: 1.0000 - val_loss: 0.5400 - val_acc: 0.8675

Epoch 00015: val_acc improved from 0.85197 to 0.86749, saving model to /data/oxford102/experiments/1546143969.900804/mobilenet_v2_1546143969.900804.h5
Epoch 16/100
17/17 [==============================] - 

17/17 [==============================] - 13s 772ms/step - loss: 1.6389 - acc: 0.6457 - val_loss: 2.1813 - val_acc: 0.4907

Epoch 00006: val_acc improved from 0.47826 to 0.49068, saving model to /data/oxford102/experiments/1546144623.9857643/mobilenet_v2_1546144623.9857643.h5
Epoch 7/100
17/17 [==============================] - 13s 766ms/step - loss: 1.5253 - acc: 0.6897 - val_loss: 2.2037 - val_acc: 0.4948

Epoch 00007: val_acc improved from 0.49068 to 0.49482, saving model to /data/oxford102/experiments/1546144623.9857643/mobilenet_v2_1546144623.9857643.h5
Epoch 8/100
17/17 [==============================] - 13s 760ms/step - loss: 1.4287 - acc: 0.7031 - val_loss: 2.1383 - val_acc: 0.5166

Epoch 00008: val_acc improved from 0.49482 to 0.51656, saving model to /data/oxford102/experiments/1546144623.9857643/mobilenet_v2_1546144623.9857643.h5
Epoch 9/100
17/17 [==============================] - 13s 761ms/step - loss: 1.4307 - acc: 0.6987 - val_loss: 2.0938 - val_acc: 0.5155

Epoch 00009: 

17/17 [==============================] - 13s 761ms/step - loss: 0.2903 - acc: 0.9732 - val_loss: 1.0747 - val_acc: 0.7464

Epoch 00009: val_acc improved from 0.73913 to 0.74638, saving model to /data/oxford102/experiments/1546145142.330233/mobilenet_v2_1546145142.330233.h5
Epoch 10/100
17/17 [==============================] - 14s 808ms/step - loss: 0.2337 - acc: 0.9862 - val_loss: 1.1198 - val_acc: 0.7461

Epoch 00010: val_acc did not improve from 0.74638
Epoch 11/100
17/17 [==============================] - 13s 744ms/step - loss: 0.2082 - acc: 0.9885 - val_loss: 1.0911 - val_acc: 0.7350

Epoch 00011: val_acc did not improve from 0.74638
Epoch 12/100
17/17 [==============================] - 13s 777ms/step - loss: 0.1778 - acc: 0.9917 - val_loss: 1.0643 - val_acc: 0.7536

Epoch 00012: val_acc improved from 0.74638 to 0.75362, saving model to /data/oxford102/experiments/1546145142.330233/mobilenet_v2_1546145142.330233.h5
Epoch 13/100
17/17 [==============================] - 13s 741ms/ste

# test some critical combinations

In [13]:
lr, momentum, nesterov, decay = 0.01, 0.9, True, 0.01

_optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
params['optimizer'] = _optimizer
params['network_name'] = "inception_resnet_v2"
_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_1 (Conv2D)               (None, 127, 127, 32) 864         input_1[0][0]                    
__________________________________________________________________________________________________
batch_normalization_1 (BatchNor (None, 127, 127, 32) 96          conv2d_1[0][0]                   
__________________________________________________________________________________________________
activation_1 (Activation)       (None, 127, 127, 32) 0           batch_normalization_1[0][0]      
__________________________________________________________________________________________________
conv2d_2 (

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
35/35 [==============================] - 95s 3s/step - loss: 2.9307 - acc: 0.3299 - val_loss: 2.1080 - val_acc: 0.4834

Epoch 00001: val_acc improved from -inf to 0.48340, saving model to /data/oxford102/experiments/1545576589.2069743/inception_resnet_v2_1545576589.2069743.h5
Epoch 2/100
35/35 [==============================] - 88s 3s/step - loss: 1.3877 - acc: 0.6668 - val_loss: 1.5633 - val_acc: 0.6128

Epoch 00002: val_acc improved from 0.48340 to 0.61284, saving model to /data/oxford102/experiments/1545576589.2069743/inception_resnet_v2_1545576589.2069743.h5
Epoch 3/100
35/35 [==============================] - 83s 2s/step - loss: 0.8951 - acc: 0.7997 - val_loss: 1.2978 - val_acc: 0.6791

Epoch 00003: val_acc improved from 0.61284 to 0.67909, saving model to /data/oxford102/experiments/1545576589.2069743/inception_resnet_v2_1545576589.2069743.h5
Epoch 4/100
35/35 [====================

In [14]:
lr, momentum, nesterov, decay = 0.001, 0.9, True, 0.01

_optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
params['optimizer'] = _optimizer
params['network_name'] = "inception_resnet_v2"
_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_2 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_204 (Conv2D)             (None, 127, 127, 32) 864         input_2[0][0]                    
__________________________________________________________________________________________________
batch_normalization_205 (BatchN (None, 127, 127, 32) 96          conv2d_204[0][0]                 
__________________________________________________________________________________________________
activation_204 (Activation)     (None, 127, 127, 32) 0           batch_normalization_205[0][0]    
__________________________________________________________________________________________________
conv2d_205

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
35/35 [==============================] - 89s 3s/step - loss: 3.7313 - acc: 0.2038 - val_loss: 2.6829 - val_acc: 0.3750

Epoch 00001: val_acc improved from -inf to 0.37500, saving model to /data/oxford102/experiments/1545577822.304359/inception_resnet_v2_1545577822.304359.h5
Epoch 2/100
35/35 [==============================] - 82s 2s/step - loss: 1.9951 - acc: 0.5204 - val_loss: 2.1360 - val_acc: 0.4793

Epoch 00002: val_acc improved from 0.37500 to 0.47930, saving model to /data/oxford102/experiments/1545577822.304359/inception_resnet_v2_1545577822.304359.h5
Epoch 3/100
35/35 [==============================] - 83s 2s/step - loss: 1.4459 - acc: 0.6726 - val_loss: 1.8687 - val_acc: 0.5383

Epoch 00003: val_acc improved from 0.47930 to 0.53830, saving model to /data/oxford102/experiments/1545577822.304359/inception_resnet_v2_1545577822.304359.h5
Epoch 4/100
35/35 [==========================

In [15]:
lr, momentum, nesterov, decay = 0.01, 0.9, True, 0.1

_optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
params['optimizer'] = _optimizer
params['network_name'] = "inception_resnet_v2"
_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_3 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_407 (Conv2D)             (None, 127, 127, 32) 864         input_3[0][0]                    
__________________________________________________________________________________________________
batch_normalization_409 (BatchN (None, 127, 127, 32) 96          conv2d_407[0][0]                 
__________________________________________________________________________________________________
activation_407 (Activation)     (None, 127, 127, 32) 0           batch_normalization_409[0][0]    
__________________________________________________________________________________________________
conv2d_408

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
35/35 [==============================] - 91s 3s/step - loss: 3.1313 - acc: 0.3087 - val_loss: 2.4322 - val_acc: 0.4141

Epoch 00001: val_acc improved from -inf to 0.41406, saving model to /data/oxford102/experiments/1545578903.619078/inception_resnet_v2_1545578903.619078.h5
Epoch 2/100
35/35 [==============================] - 82s 2s/step - loss: 1.8571 - acc: 0.5560 - val_loss: 2.0935 - val_acc: 0.4979

Epoch 00002: val_acc improved from 0.41406 to 0.49793, saving model to /data/oxford102/experiments/1545578903.619078/inception_resnet_v2_1545578903.619078.h5
Epoch 3/100
35/35 [==============================] - 83s 2s/step - loss: 1.4904 - acc: 0.6530 - val_loss: 1.8265 - val_acc: 0.5600

Epoch 00003: val_acc improved from 0.49793 to 0.56004, saving model to /data/oxford102/experiments/1545578903.619078/inception_resnet_v2_1545578903.619078.h5
Epoch 4/100
35/35 [==========================

In [17]:
lr, momentum, nesterov, decay = 0.01, 0.75, True, 0.01

_optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
params['optimizer'] = _optimizer
params['network_name'] = "inception_resnet_v2"
_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_5 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_813 (Conv2D)             (None, 127, 127, 32) 864         input_5[0][0]                    
__________________________________________________________________________________________________
batch_normalization_817 (BatchN (None, 127, 127, 32) 96          conv2d_813[0][0]                 
__________________________________________________________________________________________________
activation_813 (Activation)     (None, 127, 127, 32) 0           batch_normalization_817[0][0]    
__________________________________________________________________________________________________
conv2d_814

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
35/35 [==============================] - 93s 3s/step - loss: 2.9904 - acc: 0.3344 - val_loss: 2.1906 - val_acc: 0.4639

Epoch 00001: val_acc improved from -inf to 0.46387, saving model to /data/oxford102/experiments/1545582524.9522738/inception_resnet_v2_1545582524.9522738.h5
Epoch 2/100
35/35 [==============================] - 83s 2s/step - loss: 1.4841 - acc: 0.6588 - val_loss: 1.6920 - val_acc: 0.6025

Epoch 00002: val_acc improved from 0.46387 to 0.60248, saving model to /data/oxford102/experiments/1545582524.9522738/inception_resnet_v2_1545582524.9522738.h5
Epoch 3/100
35/35 [==============================] - 83s 2s/step - loss: 0.9773 - acc: 0.8017 - val_loss: 1.4594 - val_acc: 0.6542

Epoch 00003: val_acc improved from 0.60248 to 0.65424, saving model to /data/oxford102/experiments/1545582524.9522738/inception_resnet_v2_1545582524.9522738.h5
Epoch 4/100
35/35 [====================

# Train on half the data on each epoch (and validation)

In [20]:
lr, momentum, nesterov, decay = 0.01, 0.9, True, 0.01

_optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
params['optimizer'] = _optimizer
params['network_name'] = "inception_resnet_v2"
_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_6 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_1016 (Conv2D)            (None, 127, 127, 32) 864         input_6[0][0]                    
__________________________________________________________________________________________________
batch_normalization_1021 (Batch (None, 127, 127, 32) 96          conv2d_1016[0][0]                
__________________________________________________________________________________________________
activation_1016 (Activation)    (None, 127, 127, 32) 0           batch_normalization_1021[0][0]   
__________________________________________________________________________________________________
conv2d_101

batch_normalization_1199 (Batch (None, 6, 6, 256)    768         conv2d_1194[0][0]                
__________________________________________________________________________________________________
activation_1191 (Activation)    (None, 6, 6, 192)    0           batch_normalization_1196[0][0]   
__________________________________________________________________________________________________
activation_1194 (Activation)    (None, 6, 6, 256)    0           batch_normalization_1199[0][0]   
__________________________________________________________________________________________________
block8_4_mixed (Concatenate)    (None, 6, 6, 448)    0           activation_1191[0][0]            
                                                                 activation_1194[0][0]            
__________________________________________________________________________________________________
block8_4_conv (Conv2D)          (None, 6, 6, 2080)   933920      block8_4_mixed[0][0]             
__________

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 49s 3s/step - loss: 3.4752 - acc: 0.2344 - val_loss: 2.6433 - val_acc: 0.4023

Epoch 00001: val_acc improved from -inf to 0.40234, saving model to /data/oxford102/experiments/1545584745.7438705/inception_resnet_v2_1545584745.7438705.h5
Epoch 2/100
17/17 [==============================] - 40s 2s/step - loss: 2.4229 - acc: 0.4320 - val_loss: 2.1623 - val_acc: 0.4746

Epoch 00002: val_acc improved from 0.40234 to 0.47461, saving model to /data/oxford102/experiments/1545584745.7438705/inception_resnet_v2_1545584745.7438705.h5
Epoch 3/100
17/17 [==============================] - 40s 2s/step - loss: 1.5658 - acc: 0.6231 - val_loss: 1.7028 - val_acc: 0.5595

Epoch 00003: val_acc improved from 0.47461 to 0.55947, saving model to /data/oxford102/experiments/1545584745.7438705/inception_resnet_v2_1545584745.7438705.h5
Epoch 4/100
17/17 [====================

# Train on 1/4 the data on each epoch (1/2 for validation)

In [22]:
lr, momentum, nesterov, decay = 0.01, 0.9, True, 0.01

_optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
params['optimizer'] = _optimizer
params['network_name'] = "inception_resnet_v2"
_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_7 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_1219 (Conv2D)            (None, 127, 127, 32) 864         input_7[0][0]                    
__________________________________________________________________________________________________
batch_normalization_1225 (Batch (None, 127, 127, 32) 96          conv2d_1219[0][0]                
__________________________________________________________________________________________________
activation_1219 (Activation)    (None, 127, 127, 32) 0           batch_normalization_1225[0][0]   
__________________________________________________________________________________________________
conv2d_122

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
8/8 [==============================] - 33s 4s/step - loss: 4.0646 - acc: 0.1777 - val_loss: 3.3408 - val_acc: 0.2676

Epoch 00001: val_acc improved from -inf to 0.26758, saving model to /data/oxford102/experiments/1545587310.0326815/inception_resnet_v2_1545587310.0326815.h5
Epoch 2/100
8/8 [==============================] - 23s 3s/step - loss: 2.9899 - acc: 0.3164 - val_loss: 2.6795 - val_acc: 0.3730

Epoch 00002: val_acc improved from 0.26758 to 0.37305, saving model to /data/oxford102/experiments/1545587310.0326815/inception_resnet_v2_1545587310.0326815.h5
Epoch 3/100
8/8 [==============================] - 22s 3s/step - loss: 2.5198 - acc: 0.3984 - val_loss: 2.3645 - val_acc: 0.4251

Epoch 00003: val_acc improved from 0.37305 to 0.42511, saving model to /data/oxford102/experiments/1545587310.0326815/inception_resnet_v2_1545587310.0326815.h5
Epoch 4/100
8/8 [============================

# Train on 1/4 the data on each epoch (1/4 for validation)

In [27]:
lr, momentum, nesterov, decay = 0.01, 0.9, True, 0.01

_optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
params['optimizer'] = _optimizer
params['network_name'] = "inception_resnet_v2"
_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_8 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_1422 (Conv2D)            (None, 127, 127, 32) 864         input_8[0][0]                    
__________________________________________________________________________________________________
batch_normalization_1429 (Batch (None, 127, 127, 32) 96          conv2d_1422[0][0]                
__________________________________________________________________________________________________
activation_1422 (Activation)    (None, 127, 127, 32) 0           batch_normalization_1429[0][0]   
__________________________________________________________________________________________________
conv2d_142

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
8/8 [==============================] - 29s 4s/step - loss: 4.1199 - acc: 0.1621 - val_loss: 3.3594 - val_acc: 0.2656

Epoch 00001: val_acc improved from -inf to 0.26562, saving model to /data/oxford102/experiments/1545589254.8604958/inception_resnet_v2_1545589254.8604958.h5
Epoch 2/100
8/8 [==============================] - 19s 2s/step - loss: 3.0150 - acc: 0.2939 - val_loss: 2.7009 - val_acc: 0.3789

Epoch 00002: val_acc improved from 0.26562 to 0.37891, saving model to /data/oxford102/experiments/1545589254.8604958/inception_resnet_v2_1545589254.8604958.h5
Epoch 3/100
8/8 [==============================] - 19s 2s/step - loss: 2.5066 - acc: 0.3857 - val_loss: 2.2805 - val_acc: 0.4375

Epoch 00003: val_acc improved from 0.37891 to 0.43750, saving model to /data/oxford102/experiments/1545589254.8604958/inception_resnet_v2_1545589254.8604958.h5
Epoch 4/100
8/8 [============================

# train on 1/4, full validation

In [21]:
lr, momentum, nesterov, decay = 0.01, 0.9, True, 0.01

_optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
params['optimizer'] = _optimizer
params['network_name'] = "inception_resnet_v2"
_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_3 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_407 (Conv2D)             (None, 127, 127, 32) 864         input_3[0][0]                    
__________________________________________________________________________________________________
batch_normalization_409 (BatchN (None, 127, 127, 32) 96          conv2d_407[0][0]                 
__________________________________________________________________________________________________
activation_407 (Activation)     (None, 127, 127, 32) 0           batch_normalization_409[0][0]    
__________________________________________________________________________________________________
conv2d_408

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
8/8 [==============================] - 37s 5s/step - loss: 4.0880 - acc: 0.1475 - val_loss: 3.2685 - val_acc: 0.2578

Epoch 00001: val_acc improved from -inf to 0.25781, saving model to /data/oxford102/experiments/1545950031.2090304/inception_resnet_v2_1545950031.2090304.h5
Epoch 2/100
8/8 [==============================] - 29s 4s/step - loss: 2.9529 - acc: 0.3125 - val_loss: 2.7203 - val_acc: 0.3810

Epoch 00002: val_acc improved from 0.25781 to 0.38095, saving model to /data/oxford102/experiments/1545950031.2090304/inception_resnet_v2_1545950031.2090304.h5
Epoch 3/100
8/8 [==============================] - 29s 4s/step - loss: 2.7295 - acc: 0.3662 - val_loss: 2.5088 - val_acc: 0.3934

Epoch 00003: val_acc improved from 0.38095 to 0.39337, saving model to /data/oxford102/experiments/1545950031.2090304/inception_resnet_v2_1545950031.2090304.h5
Epoch 4/100
8/8 [============================

# train on half, full validation

In [16]:
lr, momentum, nesterov, decay = 0.01, 0.9, True, 0.01

_optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
params['optimizer'] = _optimizer
params['network_name'] = "inception_resnet_v2"
_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_1 (Conv2D)               (None, 127, 127, 32) 864         input_1[0][0]                    
__________________________________________________________________________________________________
batch_normalization_1 (BatchNor (None, 127, 127, 32) 96          conv2d_1[0][0]                   
__________________________________________________________________________________________________
activation_1 (Activation)       (None, 127, 127, 32) 0           batch_normalization_1[0][0]      
__________________________________________________________________________________________________
conv2d_2 (

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 57s 3s/step - loss: 3.5152 - acc: 0.2495 - val_loss: 2.7060 - val_acc: 0.3516

Epoch 00001: val_acc improved from -inf to 0.35156, saving model to /data/oxford102/experiments/1545946522.308495/inception_resnet_v2_1545946522.308495.h5
Epoch 2/100
17/17 [==============================] - 48s 3s/step - loss: 2.4417 - acc: 0.4141 - val_loss: 2.1425 - val_acc: 0.4700

Epoch 00002: val_acc improved from 0.35156 to 0.46998, saving model to /data/oxford102/experiments/1545946522.308495/inception_resnet_v2_1545946522.308495.h5
Epoch 3/100
17/17 [==============================] - 49s 3s/step - loss: 1.5284 - acc: 0.6343 - val_loss: 1.7780 - val_acc: 0.5404

Epoch 00003: val_acc improved from 0.46998 to 0.54037, saving model to /data/oxford102/experiments/1545946522.308495/inception_resnet_v2_1545946522.308495.h5
Epoch 4/100
17/17 [==========================

# trian on full

In [19]:
lr, momentum, nesterov, decay = 0.01, 0.9, True, 0.01

_optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
params['optimizer'] = _optimizer
params['network_name'] = "inception_resnet_v2"
_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_2 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_204 (Conv2D)             (None, 127, 127, 32) 864         input_2[0][0]                    
__________________________________________________________________________________________________
batch_normalization_205 (BatchN (None, 127, 127, 32) 96          conv2d_204[0][0]                 
__________________________________________________________________________________________________
activation_204 (Activation)     (None, 127, 127, 32) 0           batch_normalization_205[0][0]    
__________________________________________________________________________________________________
conv2d_205

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
35/35 [==============================] - 86s 2s/step - loss: 2.9350 - acc: 0.3451 - val_loss: 2.1129 - val_acc: 0.4668

Epoch 00001: val_acc improved from -inf to 0.46680, saving model to /data/oxford102/experiments/1545948437.8086205/inception_resnet_v2_1545948437.8086205.h5
Epoch 2/100
35/35 [==============================] - 79s 2s/step - loss: 1.4152 - acc: 0.6600 - val_loss: 1.6140 - val_acc: 0.5952

Epoch 00002: val_acc improved from 0.46680 to 0.59524, saving model to /data/oxford102/experiments/1545948437.8086205/inception_resnet_v2_1545948437.8086205.h5
Epoch 3/100
35/35 [==============================] - 79s 2s/step - loss: 0.8820 - acc: 0.8076 - val_loss: 1.3070 - val_acc: 0.6584

Epoch 00003: val_acc improved from 0.59524 to 0.65839, saving model to /data/oxford102/experiments/1545948437.8086205/inception_resnet_v2_1545948437.8086205.h5
Epoch 4/100
35/35 [====================

# data augmentation

In [13]:
params = {'network_name': "vgg19",
         'image_aug': True,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 256,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

In [13]:
lr, momentum, nesterov, decay = 0.01, 0.9, True, 0.01

_optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
params['optimizer'] = _optimizer
params['network_name'] = "inception_resnet_v2"
_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor, True)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_2 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_204 (Conv2D)             (None, 127, 127, 32) 864         input_2[0][0]                    
__________________________________________________________________________________________________
batch_normalization_205 (BatchN (None, 127, 127, 32) 96          conv2d_204[0][0]                 
__________________________________________________________________________________________________
activation_204 (Activation)     (None, 127, 127, 32) 0           batch_normalization_205[0][0]    
__________________________________________________________________________________________________
conv2d_205

Total params: 111,069,510
Trainable params: 56,730,726
Non-trainable params: 54,338,784
__________________________________________________________________________________________________
Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/100
17/17 [==============================] - 113s 7s/step - loss: 3.7166 - acc: 0.1969 - val_loss: 2.8673 - val_acc: 0.3145

Epoch 00001: val_acc improved from -inf to 0.31445, saving model to /data/oxford102/experiments/1545782877.3546393/inception_resnet_v2_1545782877.3546393.h5
Epoch 2/100
17/17 [==============================] - 82s 5s/step - loss: 2.4384 - acc: 0.4121 - val_loss: 2.2250 - val_acc: 0.4535

Epoch 00002: val_acc improved from 0.31445 to 0.45346, saving model to /data/oxford102/experiments/1545782877.3546393/inception_resnet_v2_1545782877.3546393.h5
Epoch 3/100
17/17 [==============================] - 74s 4s/step - loss: 1.9282 - acc: 0.5237 - val_loss: 2.0335 - val_acc: 0.4857

Epoch 00003

In [14]:
lr, momentum, nesterov, decay = 0.01, 0.9, True, 0.01

_optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
params['optimizer'] = _optimizer
params['network_name'] = "vgg19"
_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor, True)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

ResourceExhaustedError: OOM when allocating tensor with shape[256,64,256,256] and type float on /job:localhost/replica:0/task:0/device:GPU:0 by allocator GPU_0_bfc
	 [[{{node block1_conv2/convolution}} = Conv2D[T=DT_FLOAT, data_format="NCHW", dilations=[1, 1, 1, 1], padding="SAME", strides=[1, 1, 1, 1], use_cudnn_on_gpu=true, _device="/job:localhost/replica:0/task:0/device:GPU:0"](block1_conv1/Relu, block1_conv2/kernel/read)]]
Hint: If you want to see a list of allocated tensors when OOM happens, add report_tensor_allocations_upon_oom to RunOptions for current allocation info.


In [ ]:
for i in grid:
    print(i)
    lr, momentum, nesterov, decay = i
    _optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
    params['optimizer'] = _optimizer
    params['network_name'] = "vgg19"
    _model, input_processor = get_model(params["network_name"])
    train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
    train_model(params, _model, (train_generator, validation_generator))

In [ ]:
for i in grid:
    print(i)
    lr, momentum, nesterov, decay = i
    _optimizer = optimizers.SGD(lr=lr, momentum=momentum, decay=decay, nesterov=nesterov)
    params['optimizer'] = _optimizer
    params['network_name'] = "vgg16"
    _model, input_processor = get_model(params["network_name"])
    train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
    train_model(params, _model, (train_generator, validation_generator))

In [ ]:
#inception_resnet_v2, vgg16, vgg19, mobilenet_v2

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 256,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators( params["batch_size"], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

In [70]:
for batch_size in [256, 128, 64, 32]:
    for network_name in ["inception_resnet_v2", "vgg16", "vgg19"]:
        for lr in [0.001, 0.01, 0.1]:
            for optimizer in [optimizers.RMSprop(lr=lr, rho=0.9, epsilon=None, decay=0.0),
                              optimizers.SGD(lr=lr, decay=1e-6, momentum=0.9, nesterov=True), 
                              optimizers.Adagrad(lr=lr, epsilon=None, decay=0.0), 
                              optimizers.Adadelta(lr=lr, rho=0.95, epsilon=None, decay=0.0),
                              optimizers.Adam(lr=lr, beta_1=0.9, beta_2=0.999, epsilon=None, decay=0.0, amsgrad=False),
                              optimizers.Adamax(lr=lr, beta_1=0.9, beta_2=0.999, epsilon=None, decay=0.0),
                              optimizers.Nadam(lr=lr, beta_1=0.9, beta_2=0.999, epsilon=None, schedule_decay=0.004)]:
                optimizer_name = ("RMSprop" if "RMSprop" in str(optimizer) else
                                  "SGD" if "SGD" in str(optimizer) else 
                                  "Adagrad" if "Adagrad" in str(optimizer) else 
                                  "Adadelta" if "Adadelta" in str(optimizer) else 
                                  "Adam" if "Adam" in str(optimizer) else 
                                  "Adamax" if "Adamax" in str(optimizer) else 
                                  "Nadam" if "Nadam" in str(optimizer) else None)
            
            
                #inception_resnet_v2, vgg16, vgg19, mobilenet_v2

                params = {'network_name': network_name,
                         'image_aug': False,
                         'optimizer_name': optimizer_name, 
                         'optimizer': optimizer,
                         'optimizer_params': None, 
                         'batch_size': batch_size,
                         'epochs': 150,
                         'image_size': (256, 256),
                         'log_time': None}

                _model, input_processor = get_model(params["network_name"])
                train_generator, validation_generator = get_generators(batch_size, params["image_size"], input_processor)
                train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_6 (InputLayer)            (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
conv2d_813 (Conv2D)             (None, 127, 127, 32) 864         input_6[0][0]                    
__________________________________________________________________________________________________
batch_normalization_818 (BatchN (None, 127, 127, 32) 96          conv2d_813[0][0]                 
__________________________________________________________________________________________________
activation_813 (Activation)     (None, 127, 127, 32) 0           batch_normalization_818[0][0]    
__________________________________________________________________________________________________
conv2d_814

activation_992 (Activation)     (None, 6, 6, 192)    0           batch_normalization_997[0][0]    
__________________________________________________________________________________________________
activation_995 (Activation)     (None, 6, 6, 256)    0           batch_normalization_1000[0][0]   
__________________________________________________________________________________________________
block8_5_mixed (Concatenate)    (None, 6, 6, 448)    0           activation_992[0][0]             
                                                                 activation_995[0][0]             
__________________________________________________________________________________________________
block8_5_conv (Conv2D)          (None, 6, 6, 2080)   933920      block8_5_mixed[0][0]             
__________________________________________________________________________________________________
block8_5 (Lambda)               (None, 6, 6, 2080)   0           block8_4_ac[0][0]                
          

Found 4604 images belonging to 102 classes.
Found 1094 images belonging to 102 classes.
Epoch 1/150
8/8 [==============================] - 95s 12s/step - loss: 3.1314 - acc: 0.3137 - val_loss: 2.2016 - val_acc: 0.4473

Epoch 00001: val_acc improved from -inf to 0.44727, saving model to /data/oxford102/experiments/1544929307.4675195/mobilenet_v2_1544929307.4675195.h5
Epoch 2/150
8/8 [==============================] - 81s 10s/step - loss: 1.4652 - acc: 0.6521 - val_loss: 1.7202 - val_acc: 0.5722

Epoch 00002: val_acc improved from 0.44727 to 0.57216, saving model to /data/oxford102/experiments/1544929307.4675195/mobilenet_v2_1544929307.4675195.h5
Epoch 3/150
8/8 [==============================] - 67s 8s/step - loss: 0.9539 - acc: 0.7824 - val_loss: 1.2862 - val_acc: 0.6976

Epoch 00003: val_acc improved from 0.57216 to 0.69759, saving model to /data/oxford102/experiments/1544929307.4675195/mobilenet_v2_1544929307.4675195.h5
Epoch 4/150
8/8 [==============================] - 73s 9s/step -

ResourceExhaustedError: OOM when allocating tensor with shape[508,64,125,125] and type float on /job:localhost/replica:0/task:0/device:GPU:0 by allocator GPU_0_bfc
	 [[{{node conv2d_815/convolution}} = Conv2D[T=DT_FLOAT, data_format="NCHW", dilations=[1, 1, 1, 1], padding="SAME", strides=[1, 1, 1, 1], use_cudnn_on_gpu=true, _device="/job:localhost/replica:0/task:0/device:GPU:0"](activation_814/Relu, conv2d_815/kernel/read)]]
Hint: If you want to see a list of allocated tensors when OOM happens, add report_tensor_allocations_upon_oom to RunOptions for current allocation info.

	 [[{{node metrics_3/acc/Mean/_39615}} = _Recv[client_terminated=false, recv_device="/job:localhost/replica:0/task:0/device:CPU:0", send_device="/job:localhost/replica:0/task:0/device:GPU:0", send_device_incarnation=1, tensor_name="edge_4582_metrics_3/acc/Mean", tensor_type=DT_FLOAT, _device="/job:localhost/replica:0/task:0/device:CPU:0"]()]]
Hint: If you want to see a list of allocated tensors when OOM happens, a

In [16]:
#inception_resnet_v2, vgg16, vgg19, mobilenet_v2

params = {'network_name': "vgg19",
         'image_aug': False,
         'optimizer_name': "RMSprop", 
         'optimizer': optimizers.RMSprop(lr=0.001),
         'optimizer_params': None, 
         'batch_size': 256,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}

_model, input_processor = get_model(params["network_name"])
train_generator, validation_generator = get_generators(params['batch_size'], params["image_size"], input_processor)
train_model(params, _model, (train_generator, validation_generator))

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:38: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=Tensor("in..., outputs=Tensor("de...)`


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         (None, 256, 256, 3)       0         
_________________________________________________________________
block1_conv1 (Conv2D)        (None, 256, 256, 64)      1792      
_________________________________________________________________
block1_conv2 (Conv2D)        (None, 256, 256, 64)      36928     
_________________________________________________________________
block1_pool (MaxPooling2D)   (None, 128, 128, 64)      0         
_________________________________________________________________
block2_conv1 (Conv2D)        (None, 128, 128, 128)     73856     
_________________________________________________________________
block2_conv2 (Conv2D)        (None, 128, 128, 128)     147584    
_________________________________________________________________
block2_pool (MaxPooling2D)   (None, 64, 64, 128)       0         
__________

NameError: name 'num_train_img' is not defined

In [37]:
dir(optimizers.RMSprop)

['__class__',
 '__delattr__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattribute__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__le__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__slotnames__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 'from_config',
 'get_config',
 'get_gradients',
 'get_updates',
 'get_weights',
 'set_weights']

In [47]:
optimizer = optimizers.SGD

In [53]:
optimizer_name = ("RMSprop" if "RMSprop" in str(optimizer) else "SGD" if "SGD" in str(optimizer) else None)

In [54]:
optimizer_name

'SGD'

In [12]:
model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': 'vgg19',
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 128,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
35/35 [==============================] - 30s 861ms/step - loss: 3.5846 - acc: 0.2348 - val_loss: 3.0738 - val_acc: 0.3203

Epoch 00001: val_acc improved from -inf to 0.32031, saving model to /data/oxford102/experiments/1544313888.896595/mobilenet_v2_1544313888.896595.h5
Epoch 2/100
35/35 [==============================] - 24s 679ms/step - loss: 2.8652 - acc: 0.3402 - val_loss: 2.7228 - val_acc: 0.3711

Epoch 00002: val_acc improved from 0.32031 to 0.37109, saving model to /data/oxford102/experiments/1544313888.896595/mobilenet_v2_1544313888.896595.h5
Epoch 3/100
35/35 [==============================] - 24s 684ms/step - loss: 2.5635 - acc: 0.4232 - val_loss: 2.3986 - val_acc: 0.4766

Epoch 00003: val_acc improved from 0.37109 to 0.47656, saving model to /data/oxford102/experiments/1544313888.896595/mobilenet_v2_1544313888.896595.h5
Epoch 4/100
35/35 [==============================] - 24s 683ms/step - loss: 2.4074 - acc: 0.4580 - val_loss: 2.2437 - val_acc: 0.5156

Epoch 0000

In [12]:
model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': 'vgg19',
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 64,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
71/71 [==============================] - 55s 769ms/step - loss: 3.1814 - acc: 0.3072 - val_loss: 2.6400 - val_acc: 0.4320

Epoch 00001: val_acc improved from -inf to 0.43199, saving model to /data/oxford102/experiments/1544321516.4379833/mobilenet_v2_1544321516.4379833.h5
Epoch 2/100
71/71 [==============================] - 49s 685ms/step - loss: 2.4163 - acc: 0.4626 - val_loss: 2.2147 - val_acc: 0.5055

Epoch 00002: val_acc improved from 0.43199 to 0.50551, saving model to /data/oxford102/experiments/1544321516.4379833/mobilenet_v2_1544321516.4379833.h5
Epoch 3/100
71/71 [==============================] - 50s 704ms/step - loss: 1.6797 - acc: 0.6342 - val_loss: 1.9133 - val_acc: 0.5695

Epoch 00003: val_acc improved from 0.50551 to 0.56950, saving model to /data/oxford102/experiments/1544321516.4379833/mobilenet_v2_1544321516.4379833.h5
Epoch 4/100
71/71 [==============================] - 49s 688ms/step - loss: 1.5051 - acc: 0.6774 - val_loss: 1.6431 - val_acc: 0.6121

Epoc

In [12]:
model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': 'vgg19',
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 32,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
143/143 [==============================] - 104s 728ms/step - loss: 2.8257 - acc: 0.3722 - val_loss: 2.2077 - val_acc: 0.5000

Epoch 00001: val_acc improved from -inf to 0.50000, saving model to /data/oxford102/experiments/1544322364.962447/mobilenet_v2_1544322364.962447.h5
Epoch 2/100
143/143 [==============================] - 99s 692ms/step - loss: 1.6082 - acc: 0.6630 - val_loss: 1.7285 - val_acc: 0.6036

Epoch 00002: val_acc improved from 0.50000 to 0.60358, saving model to /data/oxford102/experiments/1544322364.962447/mobilenet_v2_1544322364.962447.h5
Epoch 3/100
143/143 [==============================] - 98s 684ms/step - loss: 1.0723 - acc: 0.7830 - val_loss: 1.4895 - val_acc: 0.6375

Epoch 00003: val_acc improved from 0.60358 to 0.63748, saving model to /data/oxford102/experiments/1544322364.962447/mobilenet_v2_1544322364.962447.h5
Epoch 4/100
143/143 [==============================] - 98s 683ms/step - loss: 0.7257 - acc: 0.8654 - val_loss: 1.2789 - val_acc: 0.6836

E

In [11]:
model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': 'mobilenet_v2',
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 16,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
287/287 [==============================] - 204s 711ms/step - loss: 2.1876 - acc: 0.5239 - val_loss: 1.6708 - val_acc: 0.6093

Epoch 00001: val_acc improved from -inf to 0.60930, saving model to /data/oxford102/experiments/1544324718.4162903/mobilenet_v2_1544324718.4162903.h5
Epoch 2/100
287/287 [==============================] - 196s 682ms/step - loss: 0.8537 - acc: 0.8272 - val_loss: 1.3012 - val_acc: 0.6784

Epoch 00002: val_acc improved from 0.60930 to 0.67844, saving model to /data/oxford102/experiments/1544324718.4162903/mobilenet_v2_1544324718.4162903.h5
Epoch 3/100
287/287 [==============================] - 196s 683ms/step - loss: 0.4377 - acc: 0.9240 - val_loss: 1.1310 - val_acc: 0.7269

Epoch 00003: val_acc improved from 0.67844 to 0.72693, saving model to /data/oxford102/experiments/1544324718.4162903/mobilenet_v2_1544324718.4162903.h5
Epoch 4/100
287/287 [==============================] - 196s 683ms/step - loss: 0.2630 - acc: 0.9578 - val_loss: 1.1568 - val_acc: 

In [12]:
model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': 'mobilenet_v2',
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 8,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
575/575 [==============================] - 403s 701ms/step - loss: 1.5411 - acc: 0.6723 - val_loss: 1.3399 - val_acc: 0.6692

Epoch 00001: val_acc improved from -inf to 0.66916, saving model to /data/oxford102/experiments/1544399249.5668316/mobilenet_v2_1544399249.5668316.h5
Epoch 2/100
575/575 [==============================] - 393s 683ms/step - loss: 0.3679 - acc: 0.9373 - val_loss: 1.1550 - val_acc: 0.7090

Epoch 00002: val_acc improved from 0.66916 to 0.70904, saving model to /data/oxford102/experiments/1544399249.5668316/mobilenet_v2_1544399249.5668316.h5
Epoch 3/100
575/575 [==============================] - 392s 682ms/step - loss: 0.1783 - acc: 0.9726 - val_loss: 1.1863 - val_acc: 0.7048

Epoch 00003: val_acc did not improve from 0.70904
Epoch 4/100
575/575 [==============================] - 392s 682ms/step - loss: 0.1210 - acc: 0.9810 - val_loss: 1.1200 - val_acc: 0.7149

Epoch 00004: val_acc improved from 0.70904 to 0.71492, saving model to /data/oxford102/experime

# RUN BATCHE SIZES SEQUENTIAL (no restart of kernel)

In [13]:
#run_training(model_name, _model, train_generator, validation_generator, params, num_train_img, num_val_img):
    

model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': model_name,
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 512,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
8/8 [==============================] - 9s 1s/step - loss: 0.1649 - acc: 0.9844 - val_loss: 1.1774 - val_acc: 0.7344

Epoch 00001: val_acc improved from -inf to 0.73438, saving model to /data/oxford102/experiments/1544329528.7978303/mobilenet_v2_1544329528.7978303.h5
Epoch 2/100
8/8 [==============================] - 6s 698ms/step - loss: 0.2239 - acc: 0.9727 - val_loss: 1.2865 - val_acc: 0.6875

Epoch 00002: val_acc did not improve from 0.73438
Epoch 3/100
8/8 [==============================] - 5s 683ms/step - loss: 0.2118 - acc: 0.9688 - val_loss: 1.0640 - val_acc: 0.7812

Epoch 00003: val_acc improved from 0.73438 to 0.78125, saving model to /data/oxford102/experiments/1544329528.7978303/mobilenet_v2_1544329528.7978303.h5
Epoch 4/100
8/8 [==============================] - 6s 688ms/step - loss: 0.1862 - acc: 0.9766 - val_loss: 1.4649 - val_acc: 0.6094

Epoch 00004: val_acc did not improve from 0.78125
Epoch 5/100
8/8 [==============================] - 5s 684ms/step - loss:

In [14]:
#run_training(model_name, _model, train_generator, validation_generator, params, num_train_img, num_val_img):
    

model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': model_name,
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 256,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
17/17 [==============================] - 17s 982ms/step - loss: 0.2301 - acc: 0.9651 - val_loss: 1.3921 - val_acc: 0.6250

Epoch 00001: val_acc improved from -inf to 0.62500, saving model to /data/oxford102/experiments/1544329584.4107325/mobilenet_v2_1544329584.4107325.h5
Epoch 2/100
17/17 [==============================] - 11s 661ms/step - loss: 0.1688 - acc: 0.9816 - val_loss: 1.3094 - val_acc: 0.7157

Epoch 00002: val_acc improved from 0.62500 to 0.71569, saving model to /data/oxford102/experiments/1544329584.4107325/mobilenet_v2_1544329584.4107325.h5
Epoch 3/100
17/17 [==============================] - 12s 686ms/step - loss: 0.1453 - acc: 0.9779 - val_loss: 1.2163 - val_acc: 0.6797

Epoch 00003: val_acc did not improve from 0.71569
Epoch 4/100
17/17 [==============================] - 12s 686ms/step - loss: 0.2289 - acc: 0.9596 - val_loss: 1.0969 - val_acc: 0.7344

Epoch 00004: val_acc improved from 0.71569 to 0.73438, saving model to /data/oxford102/experiments/15443295

In [15]:
#run_training(model_name, _model, train_generator, validation_generator, params, num_train_img, num_val_img):
    

model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': model_name,
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 128,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
35/35 [==============================] - 28s 793ms/step - loss: 0.2139 - acc: 0.9625 - val_loss: 1.0995 - val_acc: 0.7109

Epoch 00001: val_acc improved from -inf to 0.71094, saving model to /data/oxford102/experiments/1544329740.684749/mobilenet_v2_1544329740.684749.h5
Epoch 2/100
35/35 [==============================] - 24s 680ms/step - loss: 0.1259 - acc: 0.9837 - val_loss: 1.0764 - val_acc: 0.7578

Epoch 00002: val_acc improved from 0.71094 to 0.75781, saving model to /data/oxford102/experiments/1544329740.684749/mobilenet_v2_1544329740.684749.h5
Epoch 3/100
35/35 [==============================] - 23s 671ms/step - loss: 0.1215 - acc: 0.9857 - val_loss: 1.1856 - val_acc: 0.6913

Epoch 00003: val_acc did not improve from 0.75781
Epoch 4/100
35/35 [==============================] - 24s 678ms/step - loss: 0.1274 - acc: 0.9813 - val_loss: 1.0628 - val_acc: 0.7422

Epoch 00004: val_acc did not improve from 0.75781
Epoch 5/100
35/35 [==============================] - 24s 681m

In [16]:
#run_training(model_name, _model, train_generator, validation_generator, params, num_train_img, num_val_img):
    

model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': model_name,
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 64,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
71/71 [==============================] - 53s 753ms/step - loss: 0.1639 - acc: 0.9762 - val_loss: 1.1253 - val_acc: 0.7181

Epoch 00001: val_acc improved from -inf to 0.71815, saving model to /data/oxford102/experiments/1544329882.089569/mobilenet_v2_1544329882.089569.h5
Epoch 2/100
71/71 [==============================] - 49s 686ms/step - loss: 0.1255 - acc: 0.9815 - val_loss: 1.1536 - val_acc: 0.7261

Epoch 00002: val_acc improved from 0.71815 to 0.72610, saving model to /data/oxford102/experiments/1544329882.089569/mobilenet_v2_1544329882.089569.h5
Epoch 3/100
71/71 [==============================] - 48s 682ms/step - loss: 0.1108 - acc: 0.9824 - val_loss: 1.1970 - val_acc: 0.6931

Epoch 00003: val_acc did not improve from 0.72610
Epoch 4/100
71/71 [==============================] - 49s 685ms/step - loss: 0.1124 - acc: 0.9810 - val_loss: 1.1961 - val_acc: 0.7316

Epoch 00004: val_acc improved from 0.72610 to 0.73162, saving model to /data/oxford102/experiments/1544329882.0

In [17]:
#run_training(model_name, _model, train_generator, validation_generator, params, num_train_img, num_val_img):
    

model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': model_name,
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 32,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
143/143 [==============================] - 102s 717ms/step - loss: 0.1109 - acc: 0.9803 - val_loss: 1.1367 - val_acc: 0.7241

Epoch 00001: val_acc improved from -inf to 0.72411, saving model to /data/oxford102/experiments/1544330253.19369/mobilenet_v2_1544330253.19369.h5
Epoch 2/100
143/143 [==============================] - 98s 683ms/step - loss: 0.0811 - acc: 0.9889 - val_loss: 1.2432 - val_acc: 0.7090

Epoch 00002: val_acc did not improve from 0.72411
Epoch 3/100
143/143 [==============================] - 98s 682ms/step - loss: 0.0959 - acc: 0.9847 - val_loss: 1.1647 - val_acc: 0.7260

Epoch 00003: val_acc improved from 0.72411 to 0.72599, saving model to /data/oxford102/experiments/1544330253.19369/mobilenet_v2_1544330253.19369.h5
Epoch 4/100
143/143 [==============================] - 98s 682ms/step - loss: 0.0768 - acc: 0.9886 - val_loss: 1.1317 - val_acc: 0.7250

Epoch 00004: val_acc did not improve from 0.72599
Epoch 5/100
143/143 [==============================] - 9

In [18]:
#run_training(model_name, _model, train_generator, validation_generator, params, num_train_img, num_val_img):
    

model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': model_name,
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 16,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
287/287 [==============================] - 201s 699ms/step - loss: 0.0806 - acc: 0.9874 - val_loss: 1.1497 - val_acc: 0.7232

Epoch 00001: val_acc improved from -inf to 0.72316, saving model to /data/oxford102/experiments/1544330862.5871413/mobilenet_v2_1544330862.5871413.h5
Epoch 2/100
287/287 [==============================] - 195s 680ms/step - loss: 0.0666 - acc: 0.9901 - val_loss: 1.1626 - val_acc: 0.7218

Epoch 00002: val_acc did not improve from 0.72316
Epoch 3/100
287/287 [==============================] - 195s 679ms/step - loss: 0.0582 - acc: 0.9915 - val_loss: 1.1660 - val_acc: 0.7194

Epoch 00003: val_acc did not improve from 0.72316
Epoch 4/100
287/287 [==============================] - 195s 679ms/step - loss: 0.0541 - acc: 0.9918 - val_loss: 1.2133 - val_acc: 0.7232

Epoch 00004: val_acc improved from 0.72316 to 0.72316, saving model to /data/oxford102/experiments/1544330862.5871413/mobilenet_v2_1544330862.5871413.h5
Epoch 5/100
287/287 [========================

In [19]:
#run_training(model_name, _model, train_generator, validation_generator, params, num_train_img, num_val_img):
    

model_name = "mobilenet_v2"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': model_name,
         'image_aug': False,
         'optimizer': 'RMSprop',
          'optimizer_params': None, 
         'batch_size': 8,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.RMSprop(lr=0.001), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
575/575 [==============================] - 397s 690ms/step - loss: 0.0552 - acc: 0.9925 - val_loss: 1.2356 - val_acc: 0.7090

Epoch 00001: val_acc improved from -inf to 0.70904, saving model to /data/oxford102/experiments/1544332252.6100016/mobilenet_v2_1544332252.6100016.h5
Epoch 2/100
575/575 [==============================] - 391s 681ms/step - loss: 0.0414 - acc: 0.9940 - val_loss: 1.2587 - val_acc: 0.7142

Epoch 00002: val_acc improved from 0.70904 to 0.71422, saving model to /data/oxford102/experiments/1544332252.6100016/mobilenet_v2_1544332252.6100016.h5
Epoch 3/100
459/575 [======================>.......] - ETA: 1:05 - loss: 0.0390 - acc: 0.9948{'network_name': 'mobilenet_v2', 'image_aug': False, 'optimizer': 'RMSprop', 'optimizer_params': None, 'batch_size': 8, 'epochs': 100, 'image_size': (256, 256), 'log_time': 1544332252.6100016}


KeyboardInterrupt: 

# FINETUNE TOP LAYERS

In [ ]:
for i, layer in enumerate(base_model.layers[619:]):
    print(i, layer.name)
    layer.trainable = True

In [12]:
model_name = "vgg19"
num_train_img = 4604
num_val_img = 1094
params = {'network_name': 'vgg19',
         'image_aug': False,
         'optimizer': 'SGD',
          'optimizer_params': None, 
         'batch_size': 64,
         'epochs': 100,
         'image_size': (256, 256),
         'log_time': None}


np.random.seed(seed)
log_time = time()
params['log_time'] = log_time
batch_size = params.get("batch_size")

_model.compile(loss = "categorical_crossentropy", optimizer = optimizers.SGD(lr=0.001, momentum=0.9), metrics=["accuracy"])


base = '/data/oxford102/experiments'
path = os.path.join(base, str(log_time))
checkpoint = ModelCheckpoint(os.path.join(path, "{}_{}.h5".format(model_name, log_time)), monitor='val_acc', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_acc', min_delta=0, patience=3, verbose=1, mode='auto')
tensorboard = TensorBoard(log_dir="logs/{}".format(log_time), histogram_freq=0, write_graph=True, write_images=True)
csv_logger = CSVLogger(os.path.join(path, "{}_{}.csv".format(model_name, log_time)), append=True, separator=';')

try:
    if not os.path.exists(path):
        os.makedirs(path)
    history_callback = _model.fit_generator(
            train_generator,
            steps_per_epoch=num_train_img // batch_size,
            epochs=params.get("epochs"),
            validation_data=validation_generator,
            validation_steps=num_val_img // batch_size,
            callbacks = [checkpoint, early, tensorboard, csv_logger])
except Exception as e:
    raise(e)
finally:
    pk.dump(params, open("experimental_params/experiments_{}.pk".format(log_time), "wb"), protocol=pk.HIGHEST_PROTOCOL)
    _model.save_weights(os.path.join(path, 'model_{}_weights_final_{}.h5'.format(model_name, log_time)))  # always save your weights after training or during training
    print(params)
    params

Epoch 1/100
71/71 [==============================] - 51s 723ms/step - loss: 0.1369 - acc: 0.9802 - val_loss: 1.1463 - val_acc: 0.6834

Epoch 00001: val_acc improved from -inf to 0.68340, saving model to /data/oxford102/experiments/1544327751.1324658/vgg19_1544327751.1324658.h5
Epoch 2/100
71/71 [==============================] - 47s 665ms/step - loss: 0.1201 - acc: 0.9859 - val_loss: 1.2191 - val_acc: 0.6985

Epoch 00002: val_acc improved from 0.68340 to 0.69853, saving model to /data/oxford102/experiments/1544327751.1324658/vgg19_1544327751.1324658.h5
Epoch 3/100
71/71 [==============================] - 47s 661ms/step - loss: 0.1182 - acc: 0.9824 - val_loss: 1.0393 - val_acc: 0.7124

Epoch 00003: val_acc improved from 0.69853 to 0.71236, saving model to /data/oxford102/experiments/1544327751.1324658/vgg19_1544327751.1324658.h5
Epoch 4/100
71/71 [==============================] - 47s 663ms/step - loss: 0.1097 - acc: 0.9832 - val_loss: 1.1543 - val_acc: 0.7096

Epoch 00004: val_acc did 